**Automatic Melodic Harmonization fromSymbolic Melody Using BLSTM Networks**

Producing chord progressions from a melody is a challenging task for multiple reasons but mainly because harmonic subtleties are difficult to describe computationally. In this work, we will address the problem of automatic melodic harmonization and we will attempt to provide a proof of concept of generating chord progressions using bidirectional long short-term memory (BLSTM) networks from symbolic melodies. A dataset of lead sheets of various music genres will be used to extract meaningful melodic and harmonic information. To achieve uniformity of data, each track of the dataset will be transposed to either C major or C minor according to its initial key signature, while time signature will be normalized to avoid the imbalance of note durations. The result of the extraction will compose two-dimensional arrays consisting of twelve-note classes representing single notes in a sequence of four bars. After the pre-processing of data, the BLSTM network will be trained to generate chord progression vectors of four bars as output. Finally, a quantitative evaluation will take place where the model will be compared with other state-of-the-art algorithms to observe their performance.

In [3]:
from google.colab import drive
drive.mount("/content/drive", force_remount=True)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [4]:
import math
import numpy as np
import pandas as pd
import music21 as m21
import os
import csv
import tensorflow as tf
from keras.models import Sequential
from keras.layers import LSTM
from keras.layers import SimpleRNN
from keras.layers import Dense, Dropout
from keras.layers import TimeDistributed
from keras.layers import Bidirectional
from keras.layers import Embedding

#### Import the path of the dataset here:

In [ ]:
dataset_path = 'Wikifonia/'

#### Function for keeping the files of the dataset that contain chords and don't have errors.

In [ ]:
def check_for_chords(dataset_path):
    
    chrdFl_lst=[] # list with files that contain chords
    no_chrdFl_lst=[]

    for index,mxl in enumerate(os.listdir(dataset_path)):
        print('--',index,mxl)
        # Does the file contain chords? - initialization
        hasChords = False
        if mxl.endswith('.mxl'):
            try:
                file = dataset_path + mxl
                score = m21.converter.parse(file)
                notation = score.flat
                try:
                    for item in notation.getElementsByClass(m21.harmony.ChordSymbol):
                        print(item.figure)
                        if item:
                            print('There is at least one chord in -->', mxl)
                            hasChords = True
                            break
                except:
                    print('*****Error - file damaged*****')
            except:
                print('*****Error - file damaged*****')
                    
        if hasChords:
            chrdFl_lst.append(mxl)
            print("Has chords")
        else:
            no_chrdFl_lst.append(mxl)
            print("No chords found")
    
    return chrdFl_lst,no_chrdFl_lst

####  Test of a smaller dataset

In [ ]:
dataset = 'Wikifonia_subset_for_tests/'

files_with_chords , files_without_chords = check_for_chords(dataset)

print("Files with chords:")
for index,item in enumerate(files_with_chords): print(index,item)

print('---------')
print("Files without chords or errors:")
for index,item in enumerate(files_without_chords): print(index,item)

-- 0 . - Wien bleibt wien.mxl
C
There is at least one chord in --> . - Wien bleibt wien.mxl
Has chords
-- 1 Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
Cm
There is at least one chord in --> Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
Has chords
-- 2 Willie Garner - Super Duper Love.mxl
G
There is at least one chord in --> Willie Garner - Super Duper Love.mxl
Has chords
Files with chords:
0 . - Wien bleibt wien.mxl
1 Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
2 Willie Garner - Super Duper Love.mxl
---------
Files without chords or errors:


#### Test of the whole dataset

In [ ]:
dataset = 'Wikifonia/'

files_with_chords , files_without_chords = check_for_chords(dataset)

print("Files with chords:", len(files_with_chords))
for index,item in enumerate(files_with_chords): print(index,item)

print('---------')
print("Files without chords or errors:", len(files_without_chords))
for index,item in enumerate(files_without_chords): print(index,item)

-- 0  Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
Cm
There is at least one chord in -->  Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
Has chords
-- 1  Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl
E-M9
There is at least one chord in -->  Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl
Has chords
-- 2  Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl
Gm
There is at least one chord in -->  Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl
Has chords
-- 3  Enrique Santos Discepolo - Cambalache.mxl
C
There is at least one chord in -->  Enrique Santos Discepolo - Cambalache.mxl
Has chords
-- 4  Haydn Wood - Roses de Picardie.mxl
Dm7
There is at least one chord in -->  Haydn Wood - Roses de Picardie.mxl
Has chords
-- 5  Henry Smith 1978 - Give Thanks.mxl
G
There is at least one chord in -->  Henry Smith 1978 - Give Thanks.mxl
Has chords
-- 6  Jacques Offenbach - The Can Can

B-
There is at least one chord in --> Abner Silver, Benny Davis - There Goes My Heart.mxl
Has chords
-- 60 Abner Silver, Benny Davis - With These Hands.mxl
C
There is at least one chord in --> Abner Silver, Benny Davis - With These Hands.mxl
Has chords
-- 61 Acker Bilk and David Collet - Summer Set (Clarinet Jazz).mxl
Gpedal
There is at least one chord in --> Acker Bilk and David Collet - Summer Set (Clarinet Jazz).mxl
Has chords
-- 62 Acker Bilk, Robert Mellin - Stranger On The Shore.mxl
F
There is at least one chord in --> Acker Bilk, Robert Mellin - Stranger On The Shore.mxl
Has chords
-- 63 Acker Bilk, Robert Mellin - Stranger On The Shore.mxl.1
No chords found
-- 64 Acrylles d'Anguilla, Franz Grillparzer - Rustan's Dream.mxl
Fmaj7 alter #5
There is at least one chord in --> Acrylles d'Anguilla, Franz Grillparzer - Rustan's Dream.mxl
Has chords
-- 65 Acrylles d'Anguilla, Richard Wagner - Tristan Begins.mxl
F#/o7
There is at least one chord in --> Acrylles d'Anguilla, Richard Wagner

Am
There is at least one chord in --> Al Hoffman, Carl Lampl, Jerry Livingston - Close to You.mxl
Has chords
-- 111 Al Hoffman, Dick Manning, Bix Reichner - Papa loves Mambo.mxl
Dm7
There is at least one chord in --> Al Hoffman, Dick Manning, Bix Reichner - Papa loves Mambo.mxl
Has chords
-- 112 Al Hoffman, DickManning - Allegheny Moon.mxl
F
There is at least one chord in --> Al Hoffman, DickManning - Allegheny Moon.mxl
Has chords
-- 113 Al Hoffman, Jerry Livingston, Milton Drake - Mairzy Doats.mxl
F
There is at least one chord in --> Al Hoffman, Jerry Livingston, Milton Drake - Mairzy Doats.mxl
Has chords
-- 114 Al Hoffman, John Klenner - Heartaches.mxl
F
There is at least one chord in --> Al Hoffman, John Klenner - Heartaches.mxl
Has chords
-- 115 Al Hoffman, John Klenner - Heartaches.mxl.1
No chords found
-- 116 Al Jacobs, Jimmie Crane - Ev 'ry Day Of My Life.mxl
C
There is at least one chord in --> Al Jacobs, Jimmie Crane - Ev 'ry Day Of My Life.mxl
Has chords
-- 117 Al Jacobs, Jim

G
There is at least one chord in --> Albert Von Tilzer, Jack Norworth - I'm Sorry.mxl
Has chords
-- 166 Albert von Tilzer, Jack Norworth - Take Me Out to the Ball Game.mxl
C
There is at least one chord in --> Albert von Tilzer, Jack Norworth - Take Me Out to the Ball Game.mxl
Has chords
-- 167 Albert Von Tilzer, Junie McCree - Put Your Arms Around Me, Honey.mxl
F
There is at least one chord in --> Albert Von Tilzer, Junie McCree - Put Your Arms Around Me, Honey.mxl
Has chords
-- 168 Albert von Tilzer, Neville Fleeson - Apple Blossom Time.mxl
G
There is at least one chord in --> Albert von Tilzer, Neville Fleeson - Apple Blossom Time.mxl
Has chords
-- 169 Albert Von Tilzer, Neville Fleeson - In Apple Blossom Time.mxl
C
There is at least one chord in --> Albert Von Tilzer, Neville Fleeson - In Apple Blossom Time.mxl
Has chords
-- 170 Albert Von Tilzer, Neville Fleeson, _ - Apple Blossom Time.mxl
C
There is at least one chord in --> Albert Von Tilzer, Neville Fleeson, _ - Apple Blossom Ti

Dm6
There is at least one chord in --> Allan Roberts, Doris Fisher - Amado Mio.mxl
Has chords
-- 226 Allan Roberts, Doris Fisher - Either It's Love Or It Isn't.mxl
E-maj7
There is at least one chord in --> Allan Roberts, Doris Fisher - Either It's Love Or It Isn't.mxl
Has chords
-- 227 Allan Roberts, Doris Fisher - Into Each Life Some Rain Must Fall.mxl
F
There is at least one chord in --> Allan Roberts, Doris Fisher - Into Each Life Some Rain Must Fall.mxl
Has chords
-- 228 Allan Roberts, Doris Fisher - That Ole Devil Called Love.mxl
Fm7
There is at least one chord in --> Allan Roberts, Doris Fisher - That Ole Devil Called Love.mxl
Has chords
-- 229 Allan Roberts, Doris Fisher - You Always Hurt The One You Love.mxl
E-
There is at least one chord in --> Allan Roberts, Doris Fisher - You Always Hurt The One You Love.mxl
Has chords
-- 230 Allee Willis, Jon Lind - Boogie Wonderland.mxl
Dm
There is at least one chord in --> Allee Willis, Jon Lind - Boogie Wonderland.mxl
Has chords
-- 231 A

...

2049 George Shearing, George David Weiss - Lullaby of Birdland.mxl
2050 George Ulmer - Si tu savais.mxl
2051 George W Meyer, Edgar Leslie, Ray Goetz - For Me and My Gal.mxl
2052 George W. Duning, Steve Allen - Picnic.mxl
2053 George W. Meyer, Edgar Leslie, E. Ray Goetz - For Me And My Gal.mxl
2054 George W. Meyer, Joe  Young - Sugar.mxl
2055 George W. Warren, Daniel C. Roberts - God of Our Fathers.mxl
2056 George Weiss, Bennie Benjamin - I Don't See Me In Your Eyes Anymore.mxl
2057 George Weiss, Bennie Benjamin - That Christmas Feeling.mxl
2058 George Weiss, Hugo Peretti, Luigi Creatore - Can't Help Falling in Love.mxl
2059 George Weiss, Jerry Bock, Larry Holofcener - Mr Wonderful.mxl
2060 George Weiss, Jerry Bock, Larry Holofcener - Too Close For Comfort.mxl
2061 George Williams, Bill Jackson and Roy Straigis - So Much In Love (Transcribed).mxl
2062 George Young, Harry Vanda - Friday On My Mind.mxl
2063 George Young, Harry Vanda - Love Is In The Air.mxl
2064 Georges Auric, William Eng

2985 Jerome Kern, Leo Robin - In Love in Vain.mxl
2986 Jerome Kern, Oscar Hammerstein II - All The Things You Are.mxl
2987 Jerome Kern, Oscar Hammerstein II - Can I Forget You, Or Will My Heart Remind Me_.mxl
2988 Jerome Kern, Oscar Hammerstein II - Can't Help Lovin' Dat Man.mxl
2989 Jerome Kern, Oscar Hammerstein II - I've Told Ev'ry Little Star.mxl
2990 Jerome Kern, Oscar Hammerstein II - Make Believe.mxl
2991 Jerome Kern, Oscar Hammerstein II - Ol' Man River.mxl
2992 Jerome Kern, Oscar Hammerstein II - The Folks Who Live on the Hill.mxl
2993 Jerome Kern, Oscar Hammerstein II - The last time I saw Paris.mxl
2994 Jerome Kern, Oscar Hammerstein II - The Song Is You.mxl
2995 Jerome Kern, Oscar Hammerstein II - Why Do I Love You_.mxl
2996 Jerome Kern, Oscar Hammerstein II - Why Was I Born.mxl
2997 Jerome Kern, Oscar Hammerstein II, Otto Harbach - Who.mxl
2998 Jerome Kern, Oscar Hammerstein, Otto Harbach - I Won't Dance.mxl
2999 Jerome Kern, Otto Harbach - Smoke Gets In Your Eyes (Transcr

4085 Michael Durso, Mel Mitchell & Murl Kahn - Petticoats Of Portugal.mxl
4086 Michael Edwards, Bud Green - Once In A While .mxl
4087 Michael Edwards, Bud Green - Once In A While.mxl
4088 Michael J. Smith - Agnus Dei.mxl
4089 Michael Jackson - Beat it!.mxl
4090 Michael Jackson and Paul McCartney - Say Say Say (Transcribed).mxl
4091 Michael Joncas - On Eagle's Wings.mxl
4092 Michael Kamen - Band Of Brothers Theme.mxl
4093 Michael Kamen, Julian Lennon, Justin Clayton - Cole's Song.mxl
4094 Michael Legrand, Alan and Marilyn Bergman - The Windmills Of Your Mind.mxl
4095 Michael Legrand, Norman Gimbel - I Will Wait For You.mxl
4096 Michael Leonard, Herbert Martin - I'm All Smiles.mxl
4097 Michael Leonard, Herbert Martin - Why Did I Chose You_.mxl
4098 Michael Masser, Linda Creed - The Greatest Love Of All.mxl
4099 Michael Nolan - Little Annie Rooney.mxl
4100 Michael Perry - Calypso Carol.mxl
4101 Michael Praetorius - Lo, How A Rose E'er Blooming.mxl
4102 Michel Emer - A quoi _a sert l'amour

4894 Ronnie Self - Sweet Nothin's (Transcribed from B.L. Record).mxl
4895 Ronnie Van Zant, Ed King, Garry Rossington - Sweet Home Alabama.mxl
4896 Ronny Hinson - I'll Talk To My Father.mxl
4897 Rosendo Ruiz - Rico Vacilon.mxl
4898 Rosie Hamlin - Angel Baby.mxl
4899 Ross Bagdasarian, William Saroyan - Come On-A My House.mxl
4900 Ross MacLean, Arthur Richardson - Too Fat Polka.mxl
4901 Ross Parker - Monday Tuesday Wednesday.mxl
4902 Ross Parker, . - I'll Make Up For Ev'rything.mxl
4903 Roy Bennett, Sid Tepper - Suzy Snowflake.mxl
4904 Roy Bennett, Sid Tepper - When The Girl In Your Arms (Is The Girl In Your Heart).mxl
4905 Roy Brodsky, Sid Tepper - Red Roses for a Blue Lady.mxl
4906 Roy C Bennet & Sid Tepper - Say Something Sweet To Your Sweetheart.mxl
4907 Roy Calhoun - Teardrops.mxl
4908 Roy Hargrove - Strasbourg St. Denis.mxl
4909 Roy Ingraham, Harry Tobias - No Regrets.mxl
4910 Roy Irwin - You Need Hands.mxl
4911 Roy Jordan, Sid Bass - Soft Shoe Song.mxl
4912 Roy Orbison - Blue Bayou

5953 Wolfgang Amadeus Mozart - Laudate Dominum.mxl
5954 Wolfgang Amadeus Mozart - The Alphabet Song.mxl
5955 Woody Guthrie - So Long, It's Been Good To Know You.mxl
5956 Woody Guthrie, The Travellers - This Land is Your Land.mxl
5957 Woody Shaw - Moontrane.mxl
5958 Words and music by  LIONEL  BART - LIVING DOLL.mxl
5959 Words and music by Carol Hall - Hard Candy Christmas.mxl
5960 Words and Music by IRVING BERLIN - White Christmas.mxl
5961 Z. Elman, Johnny Mercer - And The Angels Sing.mxl
5962 Z. Fibich - POEME.mxl
5963 ZAZ, Zaz (Isabelle Geffroy) - Je Veux.mxl
5964 Zeke  - Just a little lovin'.mxl
5965 Zeke Clements, Eddy Arnold - Just a little lovin'.mxl
5966 Zequinha Abreu - Tico tico (Samba).mxl
5967 Zerkovitz Bela, Szilagyi Laszlo - Ejjel az omnibusz tetejen.mxl
5968 Zez Confrey - Stumbling.mxl
5969 Zo Elliot, Stoddard King - There's A Long, Long Trail A-Winding.mxl
5970 Zombies - Time of the Season.mxl
5971 Zsolt Dome - Sohase mondd.mxl
5972 _ - Why Don't You Believe me_.mxl
5973

In [ ]:
files_with_chords

[' Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl',
 " Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl",
 ' Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl',
 ' Enrique Santos Discepolo - Cambalache.mxl',
 ' Haydn Wood - Roses de Picardie.mxl',
 ' Henry Smith 1978 - Give Thanks.mxl',
 ' Jacques Offenbach - The Can Can (The Galop from Orpheus in the Underworld).mxl',
 ' John W Wright, John W Wright - Dancing.mxl',
 ' Kendall Hayes, Gary Walker, Kendall Hayes - Walk On By.mxl',
 ' Luigi Denza, Edward Oxenford - Funiculi,  Funicula.mxl',
 ' MGMT - ELECTRIC FEEL.mxl',
 ' Ray Davies - Sunny Afternoon.mxl',
 ' Rudolf Friml & Herbert Stothart, Otto Harbach & Oscar Hammerstein II - Indian Love Call.mxl',
 "& Nobel Prize Winner), Charles Gate Dawes (V.P. of U.S.A., Carl Sigman - It's All In The Game.mxl",
 "'Non Dignus' Traditional before 1871, From Landshuter Gesangbuch 1777 - Oh, Lord I Am Not Worthy.mxl",
 "(Unknown) Arrangement Larry

###  Check if the files that have chords (previous list) contain notes (the other way around)
Disclaimer: some of the files might not be empty even though the analysis might show that, but they contain only chords that are not associated with any notes so they are not needed.<Br>
<b>test examples:</b><br> Willie Garner - Super Duper Love
<br>. - Wien bleibt wien

In [ ]:
def check_for_notes(list_of_files_with_chords,dataset_path):
    """Use this function only after you first used check_for_chords
    to find the files that contain chords and notes. The dataset path that the previous function was
    applied to is needed as the second arguement"""
    filesWithNotesLst = []
    filesWithoutNotesLst = []
    for index,mxl in enumerate(list_of_files_with_chords):
        print('--',index,mxl)   
        hasNotes = False
        file = dataset_path + mxl
        score = m21.converter.parse(file)
        notation = score.flat

        for item in notation.getElementsByClass(m21.note.Note):
            print(item.name)
            hasNotes = True
            break

        if hasNotes:
            filesWithNotesLst.append(mxl)
        else:
            filesWithoutNotesLst.append(mxl)

    return filesWithNotesLst, filesWithoutNotesLst



In [ ]:
dataset = 'Wikifonia/'

fileLst,lstWithoutNotes = check_for_notes(files_with_chords, dataset)

-- 0  Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
C
-- 1  Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl
B-
-- 2  Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl
G
-- 3  Enrique Santos Discepolo - Cambalache.mxl
F#
-- 4  Haydn Wood - Roses de Picardie.mxl
A
-- 5  Henry Smith 1978 - Give Thanks.mxl
B
-- 6  Jacques Offenbach - The Can Can (The Galop from Orpheus in the Underworld).mxl
A
-- 7  John W Wright, John W Wright - Dancing.mxl
B
-- 8  Kendall Hayes, Gary Walker, Kendall Hayes - Walk On By.mxl
A
-- 9  Luigi Denza, Edward Oxenford - Funiculi,  Funicula.mxl
C
-- 10  MGMT - ELECTRIC FEEL.mxl
B-
-- 11  Ray Davies - Sunny Afternoon.mxl
D
-- 12  Rudolf Friml & Herbert Stothart, Otto Harbach & Oscar Hammerstein II - Indian Love Call.mxl
G
-- 13 & Nobel Prize Winner), Charles Gate Dawes (V.P. of U.S.A., Carl Sigman - It's All In The Game.mxl
A
-- 14 'Non Dignus' Traditional before 1871, From Landshuter Gesangbuch 1777 - Oh, Lor

B
-- 129 Alan Block, Don Hecht - take a letter miss jones.mxl
C
-- 130 Alan Brandt, Bob Haymes - That's All.mxl
E
-- 131 Alan Chang, Amy Foster-Gillies, Michael Buble - Home.mxl
E
-- 132 Alan Menken, Howard Ashman - Beauty and the Beast.mxl
F
-- 133 Alan Menken, Howard Ashman - Skid Row (Downtown).mxl
F
-- 134 Alan Menken, Howard Ashman - Under the Sea.mxl
D
-- 135 Alan Menken, Stephen Schwartz - Colors Of The Wind.mxl
A
-- 136 Alan Menken, Tim Rice - A WHOLE NEW WORLD.mxl
F#
-- 137 Alan Murray, Edward Lockton - I'll Walk Beside You.mxl
C
-- 138 Alan Rankin Jones - Easy Street.mxl
G
-- 139 Alan Silvestri, Glen Ballard - Believe.mxl
E
-- 140 Alan Silvestri, Glen Ballard - When Christmas Comes To Town.mxl
F
-- 141 Alanis Morissette, Glen Ballard - Ironic.mxl
A
-- 142 Albert E, Brumley, 1942 - The Blood that Stained the Old Rugged Cross.mxl
B
-- 143 Albert E. Brumley  - I'll Fly Away.mxl
F#
-- 144 Albert E. Brumley 1937 - This World Is Not My Home.mxl
F
-- 145 Albert Gamse - Scarborough F

G
-- 257 Andr_ Pat_, Marc Provance - A La P_che Aux Moules.mxl
G
-- 258 Andy Iona, Johnny Kamano, Billy Faber - Along the pineapple trail.mxl
E
-- 259 Andy Razaf and Paul Denniker - S'posin'.mxl
B-
-- 260 Ange Lorenzo, Raymond B. Egan, Jos. R. Alden, Richard A. Whiting - Sleepy Time Gal.mxl
B
-- 261 Angel Villoldo - El Choclo.mxl
A
-- 262 Anibal Troilo - Che Bandoneon.mxl
A
-- 263 Anita Kerr - A House Is Not A Home.mxl
C
-- 264 Anita Leonard, Barbara Belle, Louis Prima, Stan Rhodes - A Sunday Kind Of Love.mxl
C
-- 265 Ann Farina, Johnny Farina, Santo Farina - Sleepwalk.mxl
C
-- 266 Ann Ronell - Willow Weep For Me.mxl
D
-- 267 Anna Sosenko - Darling, Je vous aime beaucoup.mxl
A
-- 268 Annie Lennox, David A. Stewart - Sweet Dreams.mxl
E
-- 269 Annie Villeneuve -  Le sentier de neige.mxl
C
-- 270 Anonymous - A-Hunting we will go.mxl
D
-- 271 Anonymous - All My Trials.mxl
C
-- 272 Anonymous - Alouette.mxl
F
-- 273 Anonymous - Bella ciao.mxl
B
-- 274 anonymous - Dalt_l hangos.mxl
G
-- 275 a

G
-- 396 Avril Lavigne & Butch Walker - When You're Gone.mxl
F#
-- 397 Axel Stordahl and Paul Weston, Sammy Cahn - Day By Day.mxl
B
-- 398 Axel Stordahl, Paul Weston, Sammy Cahn - Day By Day.mxl
B
-- 399 Ayo - Slow, slow (Run, run).mxl
G
-- 400 B G DeSylva, Lew Brown, Ray Henderson and Al Jolson - Sonny Boy.mxl
G
-- 401 B Goodman, C Christian - Air Mail Special.mxl
A-
-- 402 B.G. DeSylva, Lew Brown & Ray Henderson - The Best Things In Life Are Free.mxl
G
-- 403 B.G.De Sylva - Wishing.mxl
B
-- 404 B.G.De Sylva, Joseph Meyer - If You Knew Susie.mxl
G
-- 405 B.G.De Sylva, Lew Brown, Ray Henderson - The Best Things In Life Are Free.mxl
G
-- 406 B.G.De Sylva_ Lew Brown and Ray Henderson - So Blue.mxl
B-
-- 407 B.G.De Sylva_ Lew Brown and Ray Henderson - Sunny Side Up.mxl
E
-- 408 B.Hilliard, D. Miles - The coffee song.mxl
G
-- 409 B52's - GIVE ME BACK MY MAN.mxl
D
-- 410 B52's - SUMMER OF LOVE.mxl
F
-- 411 Baden Powell - A Felicidade.mxl
F#
-- 412 Baden Powell - Samba triste.mxl
C
-- 413 Ba

B
-- 529 Bert Kaempfert, Charles Singleton, Eddie Snyder - Spanish Eyes.mxl
E
-- 530 Bert Kaempfert, Charles Singleton, Eddie Snyder - Strangers In The Night.mxl
F
-- 531 Bert Kaempfert, Milt Gabler - L-O-V-E.mxl
B-
-- 532 Bert Kalmar, Harry Ruby - Nevertheless (I'm In Love With You).mxl
B-
-- 533 Bert Reed., Desmond Cox, Elton Box - Quartermaster's Store.mxl
D
-- 534 Bert Reisfield, Mart Fryberg, Rolf  Marbot, Dorothy Dick - Call Me Darling.mxl
C
-- 535 Bessie Smith - Baby Doll.mxl
F
-- 536 Beverly Ross & Julius Dixon - Lollipop.mxl
G
-- 537 Beverly Ross, Edna Lewis - JUDY'S TURN TO CRY.mxl
A
-- 538 Bikini - Adj helyet.mxl
E
-- 539 Bill & Gloria Gaither - There's Something About That Name.mxl
B-
-- 540 Bill Backer, Billy Davis, Roger Cook, Roger Greenaway - I'd Like To Teach The World To Sing .mxl
D
-- 541 Bill Bird, Henri Woode, Teddy McRae - Broadway.mxl
A
-- 542 Bill Cogswell, Tommy Harrison and Johnny Noble - My Little Grass Shack In Kealakekua, Hawaii.mxl
F
-- 543 Bill Conti, Ayn

...

B-
-- 5275 Thiam and Lady Gaga - Just Dance.mxl
C#
-- 5276 Thom Bell and Linda Creed - Betcha By Golly Wow.mxl
F
-- 5277 Thom Bell and Linda Creed - You Make Me Feel Brand New.mxl
F#
-- 5278 Thomas , Harry  Brooks, Andy Razaf - Black And Blue.mxl
E
-- 5279 Thomas , Harry Brooks, Andy Razaf - Aint misbehavin'.mxl
F
-- 5280 Thomas A. Dorsey - (There'll be)  Peace in the Valley.mxl
F
-- 5281 Thomas A. Dorsey - Precious Lord, Take My Hand.mxl
C
-- 5282 Thomas E. Jones III, George Jackson - Old Time Rock And Roll.mxl
B-
-- 5283 Thomas Fats Waller, Harry Brooks, Andy Razaf - Ain't Misbehavin'.mxl
B-
-- 5284 Thomas Hastings, Augustus M. Toplady - Rock of Ages.mxl
G
-- 5285 Thomas Haynes Bayly - Long Long Ago.mxl
C
-- 5286 Thomas O. Chisholm & William J. Kirkpatrick 1897 - O To Be Like Thee.mxl
D-
-- 5287 Thomas P. Westendorf - I'll Take You Home Again, Kathleen.mxl
C
-- 5288 Thomas Salter, Eric Mouquet, Josh Groban - Awake.mxl
E-
-- 5289 Thomas Waller, Andy Razaf - Honeysuckle Rose.mxl
C
-- 5

G
-- 5424 Traditional - He Paid A Debt.mxl
G
-- 5425 Traditional - Het Dorp.mxl
D
-- 5426 Traditional - Het Levent Is Goed In't Brasantse Land.mxl
A
-- 5427 Traditional - Hij kan nie zinge nie.mxl
E
-- 5428 Traditional - Hij Was Een Smokkelaar.mxl
F
-- 5429 Traditional - Hoedje van papier.mxl
C
-- 5430 Traditional - Hollandse Medley.mxl
G#
-- 5431 Traditional - Hoor de wind waait door de bomen.mxl
D
-- 5432 Traditional - Isten szeret benn_nket.mxl
D
-- 5433 Traditional - It Came Upon a Midnight Clear.mxl
G
-- 5434 Traditional - JA, JA, SO BLAUW BLUHT DER ENZIAN.mxl
C
-- 5435 Traditional - Jolly Old Saint Nicholas.mxl
D
-- 5436 Traditional - Just a Closer Walk With Thee.mxl
F
-- 5437 Traditional - Karnavals Pot Pourri 132.mxl
C
-- 5438 Traditional - Kis karacsony, nagy karacsony.mxl
D
-- 5439 Traditional - La Golondrina.mxl
G
-- 5440 Traditional - Let Him Go, Let Him Tarry.mxl
E
-- 5441 Traditional - Mestereknek Mestere.mxl
G
-- 5442 Traditional - My Bonnie.mxl
G
-- 5443 Traditional - N

C
-- 5559 Train - Hey soul sister.mxl
F#
-- 5560 Trent Reznor - Hurt.mxl
E
-- 5561 Tschaikovski - None But The Lonely Heart.mxl
A
-- 5562 Tsiolkovsky, Lynn Paul - Where (Tsiolkovsky's 6th symphony).mxl
A
-- 5563 Tulio Trapani (Mantovani) 1954, Lee Lange (Bunny Lewis) - Cara Mia.mxl
F
-- 5564 tune_ O Sole Mio (G. Capurro), Aaron Schroeder, Wally Gold - It's Now Or Never.mxl
C
-- 5565 Turner Layton, Henry Creamer - After You've Gone.mxl
G
-- 5566 Turner Layton, Henry Creamer - Way Down Yonder In New Orleans.mxl
C
-- 5567 Turner, Turner  - Me And God.mxl
C
-- 5568 Twila Paris 1990 - How Beautiful.mxl
D
-- 5569 U2 - With or without you.mxl
D
-- 5570 Udo Jurgens - Liebe ohne Leiden.mxl
C
-- 5571 Udo Jurgens, Don Black - Walk Away.mxl
C
-- 5572 Ukrainian folksong - Gehe nicht, oh Gregor.mxl
D
-- 5573 Ukranian folk dance tune, Abraham Zevi (Zvi) Idelsohn 1918 - Hava Nagila ( ).mxl
E
-- 5574 Ulises Hermosa, Gonzalo Hermosa - Lambada - Chorando se foi.mxl
D
-- 5575 Ulrich Roever, Michael Korb -

A
-- 5739 Vaughn Horton - Ting-a-ling-a Jingle.mxl
D
-- 5740 Verdi, Temistocle Solera - Va' pensiero (Slave Song).mxl
B
-- 5741 Vernon Duke - Autumn In New York.mxl
A
-- 5742 Vernon Duke, E. Y. Harburg - April In Paris.mxl
F
-- 5743 Vernon duke, E. Y. Harburg - I Like The Likes Of You.mxl
B-
-- 5744 Vernon Duke, E. Y. Harburg - What is There to Say.mxl
E-
-- 5745 Vernon Duke, Ira Gershwin - I Can't Get Started.mxl
C
-- 5746 Vernon Duke, John LaTouche, Ted Fetter - Taking A Chance On Love.mxl
G
-- 5747 Vic Mizzy - The Addams Family Theme.mxl
F
-- 5748 Vic Mizzy, Mann Curtis - My Dreams Are Getting Better All The Time.mxl
F
-- 5749 Victor  Schertzinger, Frank Loesser - Sand In My Shoes.mxl
D
-- 5750 Victor  Schertzinger, Johnny Mercer - I Remember You.mxl
E
-- 5751 Victor  Schertzinger, Johnny Mercer - Tangerine.mxl
A
-- 5752 Victor Brasil - Creek.mxl
C
-- 5753 Victor Feldman, Milo Adamo - Haunted Ballroom.mxl
G#
-- 5754 Victor Herbert & Rida Johnson Young - I'm Falling In Love With Some

B
-- 5871 Wayne Shorter - Miyako.mxl
F#
-- 5872 Wayne Shorter - Speak No Evil.mxl
G
-- 5873 Wayne Shorter - Virgo.mxl
C
-- 5874 Wayne Shorter - Yes and No.mxl
B
-- 5875 Wayne Thomps - Always On My Mind.mxl
B
-- 5876 Wayne Walker & Lucky Moeller 1957 - Are You Sincere.mxl
F
-- 5877 Weiner, Gold - Johney Gluck - IT'S MY PARTY.mxl
F#
-- 5878 Werner Schargenberger, Alan Holt, Fini Bush - Sailor.mxl
G
-- 5879 Werner Thomas - Chicken Dance.mxl
G
-- 5880 White Stripes - YOU DON'T KNOW WHAT LOVE IS.mxl
A
-- 5881 Whyte , Morrissey  - BOXERS.mxl
A
-- 5882 Whyte, Morrissey - DON'T MAKE FUN OF DADDY'S VOICE.mxl
G#
-- 5883 Whyte, Morrissey - GLAMOROUS GLUE.mxl
G#
-- 5884 Whyte, Morrissey - IRISH BLOOD, ENGLISH HEART.mxl
A
-- 5885 Whyte, Morrissey - LET ME KISS YOU.mxl
C
-- 5886 Whyte, Morrissey - NATIONAL FRONT DISCO.mxl
C
-- 5887 Whyte, Morrissey - SOMETHING IS SQUEEZING MY SKULL.mxl
A
-- 5888 Whyte, Morrissey - WE'LL LET YOU KNOW.mxl
D
-- 5889 Wilbur Schwandt and Fabian Andre, Gus Kahn - Dream A 

In [ ]:
lstWithoutNotes

["Bobby Timmons - Moanin' Blowing Changes.mxl",
 'Daniel Mittenzwei - Dao.mxl',
 'Eric Clapton, Robert Cray - Old Love.mxl',
 'Rufus Wainwright - Sonnet 20.mxl',
 "Tom Petty - Mary Jane's Last Dance Chords.mxl",
 'Willie Garner - Super Duper Love.mxl']

#### Number of usable xml files

In [ ]:
len(fileLst)

5968

### List of files that contain notes & chords.

In [ ]:
print("\n".join(fileLst))

 Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
 Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl
 Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl
 Enrique Santos Discepolo - Cambalache.mxl
 Haydn Wood - Roses de Picardie.mxl
 Henry Smith 1978 - Give Thanks.mxl
 Jacques Offenbach - The Can Can (The Galop from Orpheus in the Underworld).mxl
 John W Wright, John W Wright - Dancing.mxl
 Kendall Hayes, Gary Walker, Kendall Hayes - Walk On By.mxl
 Luigi Denza, Edward Oxenford - Funiculi,  Funicula.mxl
 MGMT - ELECTRIC FEEL.mxl
 Ray Davies - Sunny Afternoon.mxl
 Rudolf Friml & Herbert Stothart, Otto Harbach & Oscar Hammerstein II - Indian Love Call.mxl
& Nobel Prize Winner), Charles Gate Dawes (V.P. of U.S.A., Carl Sigman - It's All In The Game.mxl
'Non Dignus' Traditional before 1871, From Landshuter Gesangbuch 1777 - Oh, Lord I Am Not Worthy.mxl
(Unknown) Arrangement Larry Johnson 2011 - I'm Too Far From Where I Started.mxl
(unknown)

####  Save the list of usable files to csv

In [ ]:
df_of_files = pd.DataFrame({'Files':fileLst})
df_of_files.to_csv("list_of_files.csv", sep=',',index=False)

df_of_files

Files
0      Alessandro Cicognini and Paul Weston, Sammy C...
1      Burt Bacharach and Carole Bayer Sager - That'...
2      Elton John, Bernie Taupin - Goodbye, Yellow B...
3             Enrique Santos Discepolo - Cambalache.mxl
4                    Haydn Wood - Roses de Picardie.mxl
...                                                 ...
5963  Zo Elliot, Stoddard King - There's A Long, Lon...
5964                   Zombies - Time of the Season.mxl
5965                      Zsolt Dome - Sohase mondd.mxl
5966                  _ - Why Don't You Believe me_.mxl
5967  _Louis Armstrong, kenny ball - Someday You'll ...

[5968 rows x 1 columns]

#### Import the list of the usable files

In [ ]:
df_files = pd.read_csv("list_of_files.csv")


df_files["Key Signature"] = ""
df_files["Time Signature"] = ""
df_files["Time Signature Numerator"] = ""
df_files["Time Signature Denominator"] = ""
df_files["Ambitus in Semitones"] = ""
df_files

Files Key Signature  \
0      Alessandro Cicognini and Paul Weston, Sammy C...                 
1      Burt Bacharach and Carole Bayer Sager - That'...                 
2      Elton John, Bernie Taupin - Goodbye, Yellow B...                 
3             Enrique Santos Discepolo - Cambalache.mxl                 
4                    Haydn Wood - Roses de Picardie.mxl                 
...                                                 ...           ...   
5963  Zo Elliot, Stoddard King - There's A Long, Lon...                 
5964                   Zombies - Time of the Season.mxl                 
5965                      Zsolt Dome - Sohase mondd.mxl                 
5966                  _ - Why Don't You Believe me_.mxl                 
5967  _Louis Armstrong, kenny ball - Someday You'll ...                 

     Time Signature Time Signature Numerator Time Signature Denominator  \
0                                                                         
1                                                                         
2                                                                         
3                                                                         
4                                                                         
...             ...                      ...                        ...   
5963                                                                      
5964                                                                      
5965                                                                      
5966                                                                      
5967                                                                      

     Ambitus in Semitones  
0                          
1                          
2                          
3                          
4                          
...                   ...  
5963                       
5964                       
5965                       
5966                       
5967                       

[5968 rows x 6 columns]

## Exctract time signature, key signature and ambitus from all the files

In [ ]:
def convertFiles(mxl):
    '''This function converts a file to notation
    Input:File name to convert without the dataset path
    Output:Notation '''
    
    file = dataset_path + mxl
    score = m21.converter.parse(file)
    notation = score.flat

    return score,notation


def keySignature(notation):
    """This function finds the keySignature of the track.
    DISCLAIMER: It is used after convertFiles.
    Input:Notation
    Output:Key signature
    """
        
    chord_symbols = m21.harmony.realizeChordSymbolDurations(notation)
    chords = m21.stream.Stream()
    for item in chord_symbols.getElementsByClass(m21.harmony.ChordSymbol):
        item.writeAsChord = True
        chords.append(item)
    chords_key = chords.analyze('key')
    
    return chords_key.name

def timeSignature(notation):
    """This function finds the time signature of the track.
    DISCLAIMER: It is used after convertFiles.
    Input:Notation
    Output 1:Time signature
    Output 2:Time signature numerator
    Output 3:Time signature denominator
    """
    timeSignature = notation.timeSignature.ratioString
    timeSignatureNumerator = notation.timeSignature.numerator
    timeSignatureDenominator= notation.timeSignature.denominator
    
    return timeSignature, timeSignatureNumerator , timeSignatureDenominator


In [ ]:
for index, mxl in df_files.iterrows():
    
    file =  mxl['Files']
    score,notation = convertFiles(file)
    keySign = keySignature(notation)
    timeSign, timeSignNU,timeSignDE = timeSignature(notation)
    
    ambitus = score.analyze('ambitus')
    ambSemitones = ambitus.semitones


    df_files.loc[df_files['Files'] == file, 'Key Signature'] = keySign
    df_files.loc[df_files['Files'] == file, 'Time Signature'] = timeSign
    df_files.loc[df_files['Files'] == file, 'Time Signature Numerator'] = timeSignNU
    df_files.loc[df_files['Files'] == file, 'Time Signature Denominator'] = timeSignDE
    df_files.loc[df_files['Files'] == file, 'Ambitus in Semitones'] = ambSemitones
 
    
    print('---------------------------------------')
    print(index, "File:", file)
    print("Key Signature:", keySign)
    print("Time Signature:", timeSign )
    print("Time Signature Numerator:", timeSignNU )
    print("Time Signature denominator:", timeSignDE )
    print("Ambitus in Semitones:", ambSemitones )

---------------------------------------
0 File:  Alessandro Cicognini and Paul Weston, Sammy Cahn - Autumn in Rome.mxl
Key Signature: A- major
Time Signature: 3/4
Time Signature Numerator: 3
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
1 File:  Burt Bacharach and Carole Bayer Sager - That's What Friends Are For.mxl
Key Signature: E- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 27
---------------------------------------
2 File:  Elton John, Bernie Taupin - Goodbye, Yellow Brick Road.mxl
Key Signature: F major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 19
---------------------------------------
3 File:  Enrique Santos Discepolo - Cambalache.mxl
Key Signature: C major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 19
---------------------------------------
4 File:  Haydn 

---------------------------------------
38 File: Aaron Schroeder, Claude DeMetrius, Bruce Sussman, Jack Feldman - Santa Bring My Baby Back (to Me).mxl
Key Signature: C major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 12
---------------------------------------
39 File: Aaron Schroeder, George Weiss - Mandolins in the Moonlight.mxl
Key Signature: B- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
40 File: Aaron Schroeder, Sid Wayne - I'm Gonna Knock On Your Door.mxl
Key Signature: F major
Time Signature: 2/2
Time Signature Numerator: 2
Time Signature denominator: 2
Ambitus in Semitones: 12
---------------------------------------
41 File: Aaron Schroeder, Wally Gold - Good Luck charm.mxl
Key Signature: B- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 14
---------------------

---------------------------------------
75 File: African-American Spiritual - Were You There.mxl
Key Signature: E- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
76 File: African-American Spiritual, Thaum Lawv - Were you there when they crucified my Lord.mxl
Key Signature: C major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
77 File: Afrojack, David Guetta, Giorgio Tuinfort, Sia Furler - Titanium.mxl
Key Signature: C minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 22
---------------------------------------
78 File: Agnes Jones, Freddy James - Unchain my Heart.mxl
Key Signature: A minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 20
---------------------------------------
79 Fil

---------------------------------------
111 File: Al Kaufman, Marty Symes - How Many Hearts Have You Broken.mxl
Key Signature: G minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
112 File: Al Lewis, Larry Stock, Vincent Rose - Blueberry Hill.mxl
Key Signature: E- major
Time Signature: 2/2
Time Signature Numerator: 2
Time Signature denominator: 2
Ambitus in Semitones: 17
---------------------------------------
113 File: Al Neiburg, Doc Dougherty, Ellis Reynolds - I'm confessin'.mxl
Key Signature: G major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 14
---------------------------------------
114 File: Al Nevins, Morty Nevins, Buck Ram - Twilight Time.mxl
Key Signature: A minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 21
---------------------------------------
115 File: Al Peshof

---------------------------------------
147 File: Albert Hay Malotte - The Lord's Prayer.mxl
Key Signature: C major
Time Signature: 6/8
Time Signature Numerator: 6
Time Signature denominator: 8
Ambitus in Semitones: 21
---------------------------------------
148 File: Albert Ketelbey  - In a Monastery Garden .mxl
Key Signature: F major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
149 File: Albert Parlow - Aambeeld-Polka.mxl
Key Signature: F major
Time Signature: 2/4
Time Signature Numerator: 2
Time Signature denominator: 4
Ambitus in Semitones: 21
---------------------------------------
150 File: Albert Von Tilzer, Jack Norworth - I'm Sorry.mxl
Key Signature: G major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 14
---------------------------------------
151 File: Albert von Tilzer, Jack Norworth - Take Me Out to the Ball Game.mxl
Key S

...

---------------------------------------
5771 File: Vincent Rose, Al Jolson, B. G. DeSylva - Avalon.mxl
Key Signature: F major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
5772 File: Vincent Rose, Al Jolson, B.G.De Sylva - Avalon.mxl
Key Signature: F major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
5773 File: Vincent Rose, Harry Owens - Linger Awhile.mxl
Key Signature: F major
Time Signature: 2/2
Time Signature Numerator: 2
Time Signature denominator: 2
Ambitus in Semitones: 17
---------------------------------------
5774 File: Vincent Scotto, Dorcas Cochran - Under The Bridges Of Paris.mxl
Key Signature: F major
Time Signature: 3/4
Time Signature Numerator: 3
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
5775 File: Vincent Scotto, Geo Koger, H

---------------------------------------
5807 File: Wagner - The Nuns' Chorus.mxl
Key Signature: C major
Time Signature: 3/4
Time Signature Numerator: 3
Time Signature denominator: 4
Ambitus in Semitones: 14
---------------------------------------
5808 File: Wally Afanasieff, Mariah Carey - All I Want For Christmas Is You.mxl
Key Signature: G major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 24
---------------------------------------
5809 File: Wally Johnson and Bob Brown - Home Among The Gum Trees.mxl
Key Signature: F major
Time Signature: 12/8
Time Signature Numerator: 12
Time Signature denominator: 8
Ambitus in Semitones: 14
---------------------------------------
5810 File: Walt Breeland and Paul Buskirk, Willie Nelson - Night Life (Guitar Solo Added).mxl
Key Signature: F major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 31
---------------------------------------
5811 File

---------------------------------------
5842 File: Wayne Shanklin - Chanson D'Amour.mxl
Key Signature: D minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 15
---------------------------------------
5843 File: Wayne Shanklin - The Big Hurt.mxl
Key Signature: A- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 11
---------------------------------------
5844 File: Wayne Shanklin 1951 - Jezebel.mxl
Key Signature: G major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
5845 File: Wayne Shanklin and George Callender - Primrose Lane (Transcribed from JW Recording).mxl
Key Signature: G minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 31
---------------------------------------
5846 File: Wayne Shorter - Footprints.mxl
Key Signature: C

---------------------------------------
5879 File: Willard Robison, Larry Conley - A Cottage For Sale.mxl
Key Signature: E- major
Time Signature: 2/2
Time Signature Numerator: 2
Time Signature denominator: 2
Ambitus in Semitones: 14
---------------------------------------
5880 File: Willem Vermandere - Blanche en zijn peird.mxl
Key Signature: A major
Time Signature: 2/4
Time Signature Numerator: 2
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
5881 File: Willi Ostermann - Rheinlandmadel.mxl
Key Signature: B- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 13
---------------------------------------
5882 File: Willi Resetarits, Georg Herrnstadt, Heinz Rudolf Unger - Jalava-Lied.mxl
Key Signature: A major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
5883 File: William  - My Guy.mxl
Key Si

---------------------------------------
5916 File: Willie Dixon - I Just Want To Make Love To You.mxl
Key Signature: D major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 14
---------------------------------------
5917 File: Willie Nelson - Angel Flying Too Close to the Ground.mxl
Key Signature: A major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
5918 File: Willie Nelson - Crazy.mxl
Key Signature: F minor
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 17
---------------------------------------
5919 File: Willie Nelson - Funny How Time Slips Away.mxl
Key Signature: B- major
Time Signature: 4/4
Time Signature Numerator: 4
Time Signature denominator: 4
Ambitus in Semitones: 16
---------------------------------------
5920 File: Willie Nelson - Hello, Walls.mxl
Key Signature: C major
Time

In [ ]:
#df_files.to_csv("list_of_files_extended.csv", sep=',',index=False)

df_files = pd.read_csv("list_of_files_extended.csv")

df_files

Files Key Signature  \
0      Alessandro Cicognini and Paul Weston, Sammy C...      A- major   
1      Burt Bacharach and Carole Bayer Sager - That'...      E- major   
2      Elton John, Bernie Taupin - Goodbye, Yellow B...       F major   
3             Enrique Santos Discepolo - Cambalache.mxl       C major   
4                    Haydn Wood - Roses de Picardie.mxl       D minor   
...                                                 ...           ...   
5963  Zo Elliot, Stoddard King - There's A Long, Lon...       G major   
5964                   Zombies - Time of the Season.mxl       E minor   
5965                      Zsolt Dome - Sohase mondd.mxl       C minor   
5966                  _ - Why Don't You Believe me_.mxl       A major   
5967  _Louis Armstrong, kenny ball - Someday You'll ...      E- major   

     Time Signature  Time Signature Numerator  Time Signature Denominator  \
0               3/4                         3                           4   
1               4/4                         4                           4   
2               4/4                         4                           4   
3               4/4                         4                           4   
4               4/4                         4                           4   
...             ...                       ...                         ...   
5963            4/4                         4                           4   
5964            4/4                         4                           4   
5965            2/4                         2                           4   
5966            4/4                         4                           4   
5967            4/4                         4                           4   

      Ambitus in Semitones  
0                       17  
1                       27  
2                       19  
3                       19  
4                       13  
...                    ...  
5963                    12  
5964                    17  
5965                     9  
5966                    19  
5967                    15  

[5968 rows x 6 columns]

#### Biggest range (ambitus) of notes of a track in corpus

In [ ]:
df_files['Ambitus in Semitones'].max()

73

#### All the unique key sigatures of the dataset

In [ ]:
np.sort(df_files["Key Signature"].unique())

array(['A major', 'A minor', 'A- major', 'B major', 'B minor', 'B- major',
       'B- minor', 'C major', 'C minor', 'C# major', 'C# minor',
       'D major', 'D minor', 'E major', 'E minor', 'E- major', 'E- minor',
       'F major', 'F minor', 'F# major', 'F# minor', 'G major', 'G minor',
       'G# minor'], dtype=object)

#### The files that contain multiple instruments with rests produce an error in the analysis therefore, we have to find them and delete them from the main dataset

In [ ]:
count=0
listOfItemsWith2Instr=[]
for index, mxl in df_files.iterrows():
    print(index)
        
    file =  mxl['Files']
    score,notation = convertFiles(file)
    if len(notation.getElementsByClass(m21.instrument.Instrument))== 2:
        count+=1
        listOfItemsWith2Instr.append(file)
    print("count:",count)

print(listOfItemsWith2Instr)

0
count: 0
1
count: 0
2
count: 0
3
count: 0
4
count: 0
5
count: 0
6
count: 0
7
count: 0
8
count: 0
9
count: 0
10
count: 0
11
count: 0
12
count: 0
13
count: 0
14
count: 0
15
count: 0
16
count: 0
17
count: 0
18
count: 1
19
count: 2
20
count: 2
21
count: 2
22
count: 2
23
count: 2
24
count: 2
25
count: 2
26
count: 2
27
count: 2
28
count: 2
29
count: 2
30
count: 2
31
count: 2
32
count: 2
33
count: 2
34
count: 2
35
count: 2
36
count: 2
37
count: 2
38
count: 2
39
count: 2
40
count: 2
41
count: 2
42
count: 2
43
count: 2
44
count: 2
45
count: 2
46
count: 2
47
count: 2
48
count: 2
49
count: 2
50
count: 2
51
count: 2
52
count: 2
53
count: 2
54
count: 2
55
count: 2
56
count: 2
57
count: 2
58
count: 2
59
count: 2
60
count: 2
61
count: 2
62
count: 2
63
count: 2
64
count: 3
65
count: 3
66
count: 3
67
count: 3
68
count: 3
69
count: 3
70
count: 3
71
count: 3
72
count: 3
73
count: 3
74
count: 3
75
count: 3
76
count: 3
77
count: 3
78
count: 3
79
count: 3
80
count: 3
81
count: 3
82
count: 3
83
count: 3
84

count: 4
642
count: 4
643
count: 4
644
count: 4
645
count: 4
646
count: 4
647
count: 4
648
count: 4
649
count: 4
650
count: 4
651
count: 4
652
count: 4
653
count: 4
654
count: 4
655
count: 4
656
count: 4
657
count: 4
658
count: 4
659
count: 4
660
count: 4
661
count: 4
662
count: 4
663
count: 4
664
count: 4
665
count: 4
666
count: 4
667
count: 4
668
count: 4
669
count: 4
670
count: 4
671
count: 4
672
count: 4
673
count: 4
674
count: 4
675
count: 4
676
count: 4
677
count: 4
678
count: 4
679
count: 4
680
count: 4
681
count: 4
682
count: 4
683
count: 4
684
count: 4
685
count: 4
686
count: 4
687
count: 4
688
count: 4
689
count: 4
690
count: 4
691
count: 4
692
count: 4
693
count: 4
694
count: 4
695
count: 4
696
count: 4
697
count: 4
698
count: 4
699
count: 4
700
count: 4
701
count: 4
702
count: 4
703
count: 4
704
count: 4
705
count: 4
706
count: 4
707
count: 4
708
count: 4
709
count: 4
710
count: 4
711
count: 4
712
count: 4
713
count: 4
714
count: 4
715
count: 4
716
count: 4
717
count: 4
718

count: 5
1253
count: 5
1254
count: 5
1255
count: 5
1256
count: 5
1257
count: 5
1258
count: 5
1259
count: 5
1260
count: 5
1261
count: 5
1262
count: 5
1263
count: 5
1264
count: 5
1265
count: 5
1266
count: 5
1267
count: 5
1268
count: 5
1269
count: 5
1270
count: 5
1271
count: 5
1272
count: 5
1273
count: 5
1274
count: 5
1275
count: 5
1276
count: 5
1277
count: 5
1278
count: 5
1279
count: 5
1280
count: 5
1281
count: 5
1282
count: 5
1283
count: 5
1284
count: 5
1285
count: 5
1286
count: 5
1287
count: 5
1288
count: 5
1289
count: 5
1290
count: 5
1291
count: 5
1292
count: 5
1293
count: 5
1294
count: 5
1295
count: 5
1296
count: 5
1297
count: 5
1298
count: 5
1299
count: 5
1300
count: 5
1301
count: 5
1302
count: 5
1303
count: 5
1304
count: 5
1305
count: 5
1306
count: 5
1307
count: 5
1308
count: 5
1309
count: 5
1310
count: 5
1311
count: 5
1312
count: 5
1313
count: 5
1314
count: 5
1315
count: 5
1316
count: 5
1317
count: 5
1318
count: 5
1319
count: 5
1320
count: 5
1321
count: 5
1322
count: 5
1323
count:

1840
count: 6
1841
count: 6
1842
count: 6
1843
count: 6
1844
count: 6
1845
count: 6
1846
count: 6
1847
count: 6
1848
count: 6
1849
count: 6
1850
count: 6
1851
count: 6
1852
count: 6
1853
count: 6
1854
count: 6
1855
count: 6
1856
count: 6
1857
count: 6
1858
count: 6
1859
count: 6
1860
count: 6
1861
count: 6
1862
count: 6
1863
count: 6
1864
count: 6
1865
count: 6
1866
count: 6
1867
count: 6
1868
count: 6
1869
count: 6
1870
count: 6
1871
count: 6
1872
count: 6
1873
count: 6
1874
count: 6
1875
count: 6
1876
count: 6
1877
count: 6
1878
count: 6
1879
count: 6
1880
count: 6
1881
count: 6
1882
count: 6
1883
count: 6
1884
count: 6
1885
count: 6
1886
count: 6
1887
count: 6
1888
count: 6
1889
count: 6
1890
count: 6
1891
count: 6
1892
count: 6
1893
count: 6
1894
count: 6
1895
count: 6
1896
count: 6
1897
count: 6
1898
count: 6
1899
count: 6
1900
count: 6
1901
count: 6
1902
count: 6
1903
count: 6
1904
count: 6
1905
count: 6
1906
count: 6
1907
count: 6
1908
count: 6
1909
count: 6
1910
count: 6
1911
c

count: 8
2426
count: 8
2427
count: 8
2428
count: 8
2429
count: 8
2430
count: 8
2431
count: 8
2432
count: 8
2433
count: 8
2434
count: 8
2435
count: 8
2436
count: 8
2437
count: 8
2438
count: 8
2439
count: 8
2440
count: 8
2441
count: 8
2442
count: 8
2443
count: 8
2444
count: 8
2445
count: 8
2446
count: 8
2447
count: 8
2448
count: 8
2449
count: 8
2450
count: 8
2451
count: 8
2452
count: 8
2453
count: 8
2454
count: 8
2455
count: 8
2456
count: 8
2457
count: 8
2458
count: 8
2459
count: 8
2460
count: 8
2461
count: 8
2462
count: 8
2463
count: 8
2464
count: 8
2465
count: 8
2466
count: 8
2467
count: 8
2468
count: 8
2469
count: 8
2470
count: 8
2471
count: 8
2472
count: 8
2473
count: 8
2474
count: 8
2475
count: 8
2476
count: 8
2477
count: 8
2478
count: 8
2479
count: 8
2480
count: 8
2481
count: 8
2482
count: 8
2483
count: 8
2484
count: 8
2485
count: 8
2486
count: 8
2487
count: 8
2488
count: 8
2489
count: 8
2490
count: 8
2491
count: 8
2492
count: 8
2493
count: 8
2494
count: 8
2495
count: 8
2496
count:

...

count: 8
3602
count: 8
3603
count: 8
3604
count: 8
3605
count: 8
3606
count: 8
3607
count: 8
3608
count: 8
3609
count: 8
3610
count: 8
3611
count: 8
3612
count: 8
3613
count: 8
3614
count: 8
3615
count: 8
3616
count: 8
3617
count: 8
3618
count: 8
3619
count: 8
3620
count: 8
3621
count: 8
3622
count: 8
3623
count: 8
3624
count: 8
3625
count: 8
3626
count: 8
3627
count: 8
3628
count: 8
3629
count: 8
3630
count: 8
3631
count: 8
3632
count: 8
3633
count: 8
3634
count: 8
3635
count: 8
3636
count: 8
3637
count: 8
3638
count: 8
3639
count: 8
3640
count: 8
3641
count: 8
3642
count: 8
3643
count: 8
3644
count: 8
3645
count: 8
3646
count: 8
3647
count: 8
3648
count: 8
3649
count: 8
3650
count: 8
3651
count: 8
3652
count: 8
3653
count: 8
3654
count: 8
3655
count: 8
3656
count: 8
3657
count: 8
3658
count: 8
3659
count: 8
3660
count: 8
3661
count: 8
3662
count: 8
3663
count: 8
3664
count: 8
3665
count: 8
3666
count: 8
3667
count: 8
3668
count: 8
3669
count: 8
3670
count: 8
3671
count: 8
3672
count:

count: 10
4191
count: 10
4192
count: 10
4193
count: 10
4194
count: 10
4195
count: 10
4196
count: 10
4197
count: 10
4198
count: 10
4199
count: 10
4200
count: 10
4201
count: 10
4202
count: 10
4203
count: 10
4204
count: 10
4205
count: 10
4206
count: 10
4207
count: 10
4208
count: 10
4209
count: 10
4210
count: 10
4211
count: 10
4212
count: 10
4213
count: 10
4214
count: 10
4215
count: 10
4216
count: 10
4217
count: 10
4218
count: 10
4219
count: 10
4220
count: 10
4221
count: 10
4222
count: 10
4223
count: 10
4224
count: 10
4225
count: 10
4226
count: 10
4227
count: 10
4228
count: 10
4229
count: 10
4230
count: 10
4231
count: 10
4232
count: 10
4233
count: 10
4234
count: 10
4235
count: 10
4236
count: 10
4237
count: 10
4238
count: 10
4239
count: 10
4240
count: 10
4241
count: 10
4242
count: 10
4243
count: 10
4244
count: 10
4245
count: 10
4246
count: 10
4247
count: 10
4248
count: 10
4249
count: 10
4250
count: 10
4251
count: 10
4252
count: 10
4253
count: 10
4254
count: 10
4255
count: 10
4256
count: 10


count: 11
4742
count: 11
4743
count: 11
4744
count: 11
4745
count: 11
4746
count: 11
4747
count: 11
4748
count: 11
4749
count: 11
4750
count: 11
4751
count: 11
4752
count: 11
4753
count: 11
4754
count: 11
4755
count: 11
4756
count: 11
4757
count: 11
4758
count: 11
4759
count: 11
4760
count: 11
4761
count: 11
4762
count: 11
4763
count: 11
4764
count: 11
4765
count: 11
4766
count: 11
4767
count: 11
4768
count: 11
4769
count: 11
4770
count: 11
4771
count: 11
4772
count: 11
4773
count: 11
4774
count: 11
4775
count: 11
4776
count: 11
4777
count: 11
4778
count: 11
4779
count: 11
4780
count: 11
4781
count: 11
4782
count: 11
4783
count: 11
4784
count: 11
4785
count: 11
4786
count: 11
4787
count: 11
4788
count: 11
4789
count: 11
4790
count: 11
4791
count: 11
4792
count: 11
4793
count: 11
4794
count: 11
4795
count: 11
4796
count: 11
4797
count: 11
4798
count: 11
4799
count: 11
4800
count: 11
4801
count: 11
4802
count: 11
4803
count: 11
4804
count: 11
4805
count: 11
4806
count: 11
4807
count: 11


count: 13
5292
count: 13
5293
count: 13
5294
count: 13
5295
count: 13
5296
count: 13
5297
count: 13
5298
count: 13
5299
count: 13
5300
count: 13
5301
count: 13
5302
count: 13
5303
count: 13
5304
count: 13
5305
count: 13
5306
count: 13
5307
count: 13
5308
count: 13
5309
count: 13
5310
count: 13
5311
count: 13
5312
count: 13
5313
count: 13
5314
count: 13
5315
count: 13
5316
count: 13
5317
count: 13
5318
count: 13
5319
count: 13
5320
count: 13
5321
count: 13
5322
count: 13
5323
count: 13
5324
count: 13
5325
count: 13
5326
count: 13
5327
count: 13
5328
count: 13
5329
count: 13
5330
count: 13
5331
count: 13
5332
count: 13
5333
count: 13
5334
count: 13
5335
count: 13
5336
count: 13
5337
count: 13
5338
count: 13
5339
count: 13
5340
count: 13
5341
count: 13
5342
count: 13
5343
count: 13
5344
count: 13
5345
count: 13
5346
count: 13
5347
count: 13
5348
count: 13
5349
count: 13
5350
count: 13
5351
count: 13
5352
count: 13
5353
count: 13
5354
count: 13
5355
count: 13
5356
count: 13
5357
count: 13


count: 17
5845
count: 17
5846
count: 17
5847
count: 17
5848
count: 17
5849
count: 17
5850
count: 17
5851
count: 17
5852
count: 17
5853
count: 17
5854
count: 17
5855
count: 17
5856
count: 17
5857
count: 17
5858
count: 17
5859
count: 17
5860
count: 17
5861
count: 17
5862
count: 17
5863
count: 17
5864
count: 17
5865
count: 17
5866
count: 17
5867
count: 17
5868
count: 17
5869
count: 17
5870
count: 17
5871
count: 17
5872
count: 17
5873
count: 17
5874
count: 17
5875
count: 17
5876
count: 17
5877
count: 17
5878
count: 17
5879
count: 17
5880
count: 17
5881
count: 17
5882
count: 17
5883
count: 17
5884
count: 17
5885
count: 17
5886
count: 17
5887
count: 17
5888
count: 17
5889
count: 17
5890
count: 17
5891
count: 17
5892
count: 17
5893
count: 17
5894
count: 17
5895
count: 17
5896
count: 17
5897
count: 17
5898
count: 17
5899
count: 17
5900
count: 17
5901
count: 17
5902
count: 17
5903
count: 17
5904
count: 17
5905
count: 17
5906
count: 17
5907
count: 17
5908
count: 17
5909
count: 17
5910
count: 17


In [ ]:
listOfItemsWith2Instr

['.onbekend, onbekend - Cill Chais.mxl',
 '.onbekend, onbekend - The Rose Of Allendale.mxl',
 'Adam Levine, Jesse Charmichael - This love.mxl',
 'Aphex Twin - Flim.mxl',
 'Clare Fischer - Gaviota.mxl',
 'DJ Antoine - Ma Cherie (simple).mxl',
 'Glen Hansard - Falling Slowly.mxl',
 'Hans-Martin Majewski  - So ein Pony - Immenhof.mxl',
 'Lucio Dalla - Caruso.mxl',
 'modulator - Modulaties.mxl',
 'R. Froger - Alles Kan Een Mens Gelukkig Maken.mxl',
 'Speyerer Gesangbuch, Mainz - Es ist ein Ros entsprungen.mxl',
 'Sublime - Santeria.mxl',
 "Traditional tune_  Top o' Cork Road, Max T. Krone - 'Tis Irish I Am.mxl",
 'Unknown - MEXICO.mxl',
 'Volksweise - Alle Jahre Wieder.mxl',
 'Volksweise aus Tirol - Es wird scho glei dumpa.mxl']

In [ ]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None) 

In [ ]:
df_files

Files Key Signature  \
0      Alessandro Cicognini and Paul Weston, Sammy C...      A- major   
1      Burt Bacharach and Carole Bayer Sager - That'...      E- major   
2      Elton John, Bernie Taupin - Goodbye, Yellow B...       F major   
3             Enrique Santos Discepolo - Cambalache.mxl       C major   
4                    Haydn Wood - Roses de Picardie.mxl       D minor   
...                                                 ...           ...   
5963  Zo Elliot, Stoddard King - There's A Long, Lon...       G major   
5964                   Zombies - Time of the Season.mxl       E minor   
5965                      Zsolt Dome - Sohase mondd.mxl       C minor   
5966                  _ - Why Don't You Believe me_.mxl       A major   
5967  _Louis Armstrong, kenny ball - Someday You'll ...      E- major   

     Time Signature  Time Signature Numerator  Time Signature Denominator  \
0               3/4                         3                           4   
1               4/4                         4                           4   
2               4/4                         4                           4   
3               4/4                         4                           4   
4               4/4                         4                           4   
...             ...                       ...                         ...   
5963            4/4                         4                           4   
5964            4/4                         4                           4   
5965            2/4                         2                           4   
5966            4/4                         4                           4   
5967            4/4                         4                           4   

      Ambitus in Semitones  
0                       17  
1                       27  
2                       19  
3                       19  
4                       13  
...                    ...  
5963                    12  
5964                    17  
5965                     9  
5966                    19  
5967                    15  

[5968 rows x 6 columns]

In [ ]:
# List of indexes of the files that we want to delete from the dataframe

index_list=[]
for item in listOfItemsWith2Instr:
    index_list.append(df_files.index[df_files['Files'] == item].tolist())
    
# Flatten the list of indexes that we want to remove
flat_list = [item for sublist in index_list for item in sublist]

# We add manually the indexes of files with errors that were found during previous experiments
flat_list.extend([327,1219,1428,1804,2150,3061,3256,3671,4062])
flat_list.sort()

# Remove the files from the dataset and reset the index
df_files.drop(flat_list, inplace=True)
df_files.reset_index(drop=True, inplace=True)

#### Save/read the final list of files in csv format.

In [ ]:
#df_files.to_csv("final_list_of_files.csv", sep=',',index=False)

df_files = pd.read_csv("final_list_of_files.csv")

df_files

Files Key Signature  \
0      Alessandro Cicognini and Paul Weston, Sammy C...      A- major   
1      Burt Bacharach and Carole Bayer Sager - That'...      E- major   
2      Elton John, Bernie Taupin - Goodbye, Yellow B...       F major   
3             Enrique Santos Discepolo - Cambalache.mxl       C major   
4                    Haydn Wood - Roses de Picardie.mxl       D minor   
...                                                 ...           ...   
5937  Zo Elliot, Stoddard King - There's A Long, Lon...       G major   
5938                   Zombies - Time of the Season.mxl       E minor   
5939                      Zsolt Dome - Sohase mondd.mxl       C minor   
5940                  _ - Why Don't You Believe me_.mxl       A major   
5941  _Louis Armstrong, kenny ball - Someday You'll ...      E- major   

     Time Signature  Time Signature Numerator  Time Signature Denominator  \
0               3/4                         3                           4   
1               4/4                         4                           4   
2               4/4                         4                           4   
3               4/4                         4                           4   
4               4/4                         4                           4   
...             ...                       ...                         ...   
5937            4/4                         4                           4   
5938            4/4                         4                           4   
5939            2/4                         2                           4   
5940            4/4                         4                           4   
5941            4/4                         4                           4   

      Ambitus in Semitones  
0                       17  
1                       27  
2                       19  
3                       19  
4                       13  
...                    ...  
5937                    12  
5938                    17  
5939                     9  
5940                    19  
5941                    15  

[5942 rows x 6 columns]

#### Our final dataframe contains 5942 file names with files that can potentially be analysed

# Build the main dataframe of notes and features for the model

#### An example of a file's content

In [ ]:
mxl = " Kendall Hayes, Gary Walker, Kendall Hayes - Walk On By.mxl"
score,notation = convertFiles(mxl)
score.show('text')

{0.0} <music21.text.TextBox "Walk on by">
{0.0} <music21.text.TextBox "Kendall Ha...">
{0.0} <music21.metadata.Metadata object at 0x000002040259A888>
{0.0} <music21.stream.Part Electric Piano>
    {0.0} <music21.instrument.Instrument 'P1: Electric Piano: Electric Piano'>
    {0.0} <music21.stream.Measure 1 offset=0.0>
        {0.0} <music21.layout.SystemLayout>
        {0.0} <music21.clef.TrebleClef>
        {0.0} <music21.key.Key of C major>
        {0.0} <music21.meter.TimeSignature 4/4>
        {0.0} <music21.note.Rest rest>
        {2.0} <music21.note.Note A>
        {3.0} <music21.note.Note B>
    {0.0} <music21.spanner.RepeatBracket 1 <music21.stream.Measure 32 offset=0.0>>
    {0.0} <music21.spanner.RepeatBracket 2 <music21.stream.Measure 34 offset=0.0>>
    {4.0} <music21.stream.Measure 2 offset=4.0>
        {0.0} <music21.bar.Repeat direction=start>
        {0.0} <music21.harmony.ChordSymbol C>
        {0.0} <music21.note.Note C>
        {2.0} <music21.note.Note B>
        {3.

## For every measure, extract measure number, note or rest, note pitch class, chord, chord inversion, duration in quarternotes, beat position, offset and create a dataframe for each song

### Extraction of features for each track and building of the main dataframe of our model.

In [ ]:
def NumberOfSemitonesToTransposeToC(mxl):
    """Checks the key signature of the track and returns the number of semitones to transpose to C.
    Input:mxl
    Output:Number of semitones"""

    KeySignature = df_files.loc[df_files['Files'] == mxl, ['Key Signature']].values[0][0][:2]

    # We use the semitones that relate only to the used key signatures that were detected earlier
    semitones = {
        'A ':9,
        'A-':8,
        'B-':10,
        'B ':11,
        'C ':0,
        'C#':1,
        'D ':2,
        'E-':3,
        'E ':4,
        'F ':5,
        'F#':6,
        'G ':7,
        'G#':8
    }
 
    return semitones.get(KeySignature)



def appendFeatures(bar, noteOrRest, df, currentChord , 
                   item_pitch , item_pitch_midi ,
                   item_pitch_name, item_pitch_class,octave):

    chordPitchClasses = [str(p) for p in currentChord.pitches]
    chordPitchNumericalClasses = [str(p) for p in currentChord.pitchClasses]
    
    df = df.append({'Note': item_pitch,
                'Midi Note': item_pitch_midi,
                'Note Pitch Class': item_pitch_name,
                'Note Pitch Numerical Class': item_pitch_class,
                'Octave': octave,
                'Chord': currentChord.figure,
                'Chord Pitch Classes': chordPitchClasses,
                'Chord Pitch Numerical Classes': chordPitchNumericalClasses,
                'Chord Inversion': currentChord.inversion(),
                'Duration': noteOrRest.duration.quarterLength,
                'Bar': bar.number,
                'Beat Position': noteOrRest.beat},
                #'Offset': noteOrRest.offset},
                ignore_index=True)
    
    
    return df
  
    
def analyseMeasureElements(score):
    score_measures = score.getElementsByClass(m21.stream.Part)[0].getElementsByClass(m21.stream.Measure)
    
    # Dataframe initialization
    df_notes = pd.DataFrame(columns=['Note',
                                'Midi Note',
                                'Note Pitch Class',
                                'Note Pitch Numerical Class',
                                'Octave',
                                'Chord',
                                'Chord Pitch Classes',
                                'Chord Pitch Numerical Classes',
                                'Chord Inversion',
                                'Duration',
                                'Bar',
                                'Beat Position'#,
                                #'Offset'
                                ])


    # Iterate over the measures/bars of the song
    for measure in score_measures:
        
        # For every item in the measure/bar, iterate
        for index, item in enumerate(measure):
            
            # Use of exception, because in some cases the first bars are incomplete 
            # and might not contain assigned chords.
            try:

                # Chord Symbols precede notes, therefore they can be assigned to notes firstly. 
                if type(item) is m21.harmony.ChordSymbol:
                    current_chord=item     

                elif type(item) is m21.note.Note:                
                    df_notes = appendFeatures(measure, item, df_notes, current_chord , 
                                              item.pitch, item.pitch.midi, item.pitch.name,
                                              item.pitch.pitchClass, item.pitch.octave)

                elif type(item) is m21.note.Rest:
                    df_notes = appendFeatures(measure, item, df_notes, current_chord , 
                                              item.name, item.name, item.name, 12, 0)

            except:
                #print("The measure/bar is incomplete or doesn't contain chords")
                continue
                
                
                
    return df_notes


def transposeDF(df_m,amount):
    
    df_m = np.where(df_m == 12, 1000, df_m)
    df_m = np.where(df_m - amount >= 0, df_m - amount, 12-abs(df_m - amount)) 
    df_m = np.where(df_m == 1000 - amount, 12, df_m)
    
    df_updated = pd.Series(df_m)
    return df_updated


def BuildModelDF(Mxml, df):
    # Model Dataframe initialization
    df_mod = pd.DataFrame(columns=[
                                'Transposed Note Pitch Numerical Class',
                                'Octave',
                                'Duration',
                                'Bar',
                                'Beat Position',
                                'Key Major',
                                'Key Minor',
                                'Time Signature Numerator',
                                'Time Signature Denominator',
                                'Chord Inversion'
                                ])
    
    # Find the semitones needed to transpose to C
    semitones = NumberOfSemitonesToTransposeToC(Mxml)

    
    df_mod[['Transposed Note Pitch Numerical Class',
            'Octave', 'Duration', 'Bar', 
            'Beat Position', 'Chord Inversion']] = df[['Note Pitch Numerical Class', 'Octave', 
                                                       'Duration', 'Bar', 'Beat Position', 'Chord Inversion']]    


    
    
    # DF of isolated chord notes
    df_chordNotes = df.apply(lambda x: pd.Series(x['Chord Pitch Numerical Classes']),axis=1)

    if len(df_chordNotes.columns) is not 8:
        addThisNumberOfEmptyColumns = 8-len(df_chordNotes.columns)
        new_columns =list(range(len(df_chordNotes.columns),len(df_chordNotes.columns)+addThisNumberOfEmptyColumns))
    
    # If the number of columns is not 8 (the max number of chord notes) add an appropriate amount of empty rows
    df_chordNotes = df_chordNotes.reindex(df_chordNotes.columns.tolist() + new_columns, axis=1)
    
    df_chordNotes.columns = ['Chord Note 1',
                                'Chord Note 2',
                                'Chord Note 3',
                                'Chord Note 4',
                                'Chord Note 5',
                                'Chord Note 6',
                                'Chord Note 7',
                                'Chord Note 8' ]
    
    

    #Concatinate
    df_mod = pd.concat([df_mod, df_chordNotes], axis=1, sort=False)
    
    
    
    #Transpose Notes and Chord Notes
    df_mod['Transposed Note Pitch Numerical Class'] = transposeDF(df_mod['Transposed Note Pitch Numerical Class'],semitones)
    
    df_mod['Chord Note 1'] = pd.to_numeric(df_mod['Chord Note 1'], downcast='integer')
    df_mod['Chord Note 2'] = pd.to_numeric(df_mod['Chord Note 2'], downcast='integer')
    df_mod['Chord Note 3'] = pd.to_numeric(df_mod['Chord Note 3'], downcast='integer')
    df_mod['Chord Note 4'] = pd.to_numeric(df_mod['Chord Note 4'], downcast='integer')
    df_mod['Chord Note 5'] = pd.to_numeric(df_mod['Chord Note 5'], downcast='integer')
    df_mod['Chord Note 6'] = pd.to_numeric(df_mod['Chord Note 6'], downcast='integer')
    df_mod['Chord Note 7'] = pd.to_numeric(df_mod['Chord Note 7'], downcast='integer')
    df_mod['Chord Note 8'] = pd.to_numeric(df_mod['Chord Note 8'], downcast='integer')
    
    df_mod['Chord Note 1'] = transposeDF(df_mod['Chord Note 1'],semitones)
    df_mod['Chord Note 2'] = transposeDF(df_mod['Chord Note 2'],semitones)
    df_mod['Chord Note 3'] = transposeDF(df_mod['Chord Note 3'],semitones)
    df_mod['Chord Note 4'] = transposeDF(df_mod['Chord Note 4'],semitones)
    df_mod['Chord Note 5'] = transposeDF(df_mod['Chord Note 5'],semitones)
    df_mod['Chord Note 6'] = transposeDF(df_mod['Chord Note 6'],semitones)
    df_mod['Chord Note 7'] = transposeDF(df_mod['Chord Note 7'],semitones)
    df_mod['Chord Note 8'] = transposeDF(df_mod['Chord Note 8'],semitones)

    # Assign the key signature
    KeySignat = df_files.loc[df_files['Files'] == Mxml, ['Key Signature']].values[0]

    if 'major' in str(KeySignat):
        df_mod.loc[:,'Key Major'] = 1
        df_mod.loc[:,'Key Minor'] = 0
        
    elif 'minor' in str(KeySignat):
        df_mod.loc[:,'Key Major'] = 0
        df_mod.loc[:,'Key Minor'] = 1
    
    # Assign the time signature
    numerator = df_files.loc[df_files['Files'] == Mxml, ['Time Signature Numerator']].values[0][0]
    df_mod.loc[:,'Time Signature Numerator'] = numerator
    
    denominator = df_files.loc[df_files['Files'] == Mxml, ['Time Signature Denominator']].values[0][0]
    df_mod.loc[:,'Time Signature Denominator'] = denominator

    
    # Fill the NaN values with 13 that is the "assigned" class of rest
    df_mod.iloc[:,10:] = df_mod.iloc[:,10:].fillna(12).astype(int)
    
    return df_mod

### Build the main dataframe

In [ ]:
MainDataFrame = pd.DataFrame(columns=[
                                'Transposed Note Pitch Numerical Class',
                                'Octave',
                                'Duration',
                                'Bar',
                                'Beat Position',
                                'Key Major',
                                'Key Minor',
                                'Time Signature Numerator',
                                'Time Signature Denominator',
                                'Chord Inversion',
                                'Chord Note 1',
                                'Chord Note 2',
                                'Chord Note 3',
                                'Chord Note 4',
                                'Chord Note 5',
                                'Chord Note 6',
                                'Chord Note 7',
                                'Chord Note 8' 
                                ])

# Iterate over dataset's rows
for index, mxl in df_files.iterrows():
    
        
    file =  mxl['Files']
    
    #print(index, mxl)
    score,notation = convertFiles(file)
    
    df_example = analyseMeasureElements(score)
    df_model = BuildModelDF(file, df_example)

    MainDataFrame = pd.concat([MainDataFrame, df_model], ignore_index=True)

    if (index%10 == 0 and index is not 0):
        print(index, "Files Analysed")
    

    
MainDataFrame.to_csv("MainDataFrame.csv", sep=',',index=False)
#MainDataFrame

C:\Users\Myrsini\anaconda3\lib\site-packages\ipykernel_launcher.py:110: RuntimeWarning: invalid value encountered in greater_equal


10 Files Analysed
20 Files Analysed
30 Files Analysed
40 Files Analysed
50 Files Analysed
60 Files Analysed
70 Files Analysed
80 Files Analysed
90 Files Analysed
100 Files Analysed
110 Files Analysed
120 Files Analysed
130 Files Analysed
140 Files Analysed
150 Files Analysed
160 Files Analysed
170 Files Analysed
180 Files Analysed
190 Files Analysed
200 Files Analysed
210 Files Analysed
220 Files Analysed
230 Files Analysed
240 Files Analysed
250 Files Analysed
260 Files Analysed
270 Files Analysed
280 Files Analysed
290 Files Analysed
300 Files Analysed
310 Files Analysed
320 Files Analysed
330 Files Analysed
340 Files Analysed
350 Files Analysed
360 Files Analysed
370 Files Analysed
380 Files Analysed
390 Files Analysed
400 Files Analysed
410 Files Analysed
420 Files Analysed
430 Files Analysed
440 Files Analysed
450 Files Analysed
460 Files Analysed
470 Files Analysed
480 Files Analysed
490 Files Analysed
500 Files Analysed
510 Files Analysed
520 Files Analysed
530 Files Analysed
54

4170 Files Analysed
4180 Files Analysed
4190 Files Analysed
4200 Files Analysed
4210 Files Analysed
4220 Files Analysed
4230 Files Analysed
4240 Files Analysed
4250 Files Analysed
4260 Files Analysed
4270 Files Analysed
4280 Files Analysed
4290 Files Analysed
4300 Files Analysed
4310 Files Analysed
4320 Files Analysed
4330 Files Analysed
4340 Files Analysed
4350 Files Analysed
4360 Files Analysed
4370 Files Analysed
4380 Files Analysed
4390 Files Analysed
4400 Files Analysed
4410 Files Analysed
4420 Files Analysed
4430 Files Analysed
4440 Files Analysed
4450 Files Analysed
4460 Files Analysed
4470 Files Analysed
4480 Files Analysed
4490 Files Analysed
4500 Files Analysed
4510 Files Analysed
4520 Files Analysed
4530 Files Analysed
4540 Files Analysed
4550 Files Analysed
4560 Files Analysed
4570 Files Analysed
4580 Files Analysed
4590 Files Analysed
4600 Files Analysed
4610 Files Analysed
4620 Files Analysed
4630 Files Analysed
4640 Files Analysed
4650 Files Analysed
4660 Files Analysed


In [ ]:
MainDataFrame

Transposed Note Pitch Numerical Class  ...  Chord Note 8
0                                           4  ...            12
1                                           6  ...            12
2                                           7  ...            12
3                                          11  ...            12
4                                           4  ...            12
...                                       ...  ...           ...
925218                                      4  ...            12
925219                                      7  ...            12
925220                                      0  ...            12
925221                                      0  ...            12
925222                                     12  ...            12

[925223 rows x 18 columns]

In [ ]:
# pd.set_option('display.max_rows', 10)

In [ ]:
# Load main df

#google drive mount path
drive_path = "/content/drive/My Drive/Colab Notebooks/MainDataFrame.csv"
MainDataFrame = pd.read_csv(drive_path)

MainDataFrame

Transposed Note Pitch Numerical Class  ...  Chord Note 8
0                                           4  ...            12
1                                           6  ...            12
2                                           7  ...            12
3                                          11  ...            12
4                                           4  ...            12
...                                       ...  ...           ...
925218                                      4  ...            12
925219                                      7  ...            12
925220                                      0  ...            12
925221                                      0  ...            12
925222                                     12  ...            12

[925223 rows x 18 columns]

## **Data Preprocessing**




### **Time Signature Normalization - Balancing time**

In [ ]:
# Replace fractions with integers
MainDataFrame["Duration"] = MainDataFrame["Duration"].replace({'1/3':'0.33', '4/3':'1.33', '2/3': 0.66 , '1/6': 0.17 ,
                                                               '1/12': 0.08 , '1/10':0.1 , '1/5': 0.2, '8/3': 2.66 ,'3/10': 0.3, '2/5': 0.4})

# Transform the type to integers
for col in MainDataFrame.columns: 
    MainDataFrame[col] = MainDataFrame[col].astype('int', errors='ignore')

# New column with balanced duration
MainDataFrame.insert(3, 'Balanced Duration', (MainDataFrame['Time Signature Denominator']/MainDataFrame['Time Signature Numerator'])*MainDataFrame["Duration"].astype(float))


In [ ]:
#MainDataFrame.to_csv("MainDataFrameBalanced.csv", sep=',',index=False)
drive_path2 = "/content/drive/My Drive/Colab Notebooks/MainDataFrameBalanced.csv"
MainDataFrameBalanced = pd.read_csv(drive_path2)
MainDataFrameBalanced

Transposed Note Pitch Numerical Class  ...  Chord Note 8
0                                           4  ...            12
1                                           6  ...            12
2                                           7  ...            12
3                                          11  ...            12
4                                           4  ...            12
...                                       ...  ...           ...
925218                                      4  ...            12
925219                                      7  ...            12
925220                                      0  ...            12
925221                                      0  ...            12
925222                                     12  ...            12

[925223 rows x 19 columns]

In [ ]:
# Amount of notes less than a 16nth
MainDataFrameBalanced[MainDataFrameBalanced['Balanced Duration'] < 0.25].count()
#MainDataFrameBalanced[MainDataFrameBalanced['Balanced Duration'] < 0.25].count()/len(MainDataFrameBalanced.index))*100

Transposed Note Pitch Numerical Class    3256
Octave                                   3256
Duration                                 3256
Balanced Duration                        3256
Bar                                      3256
Beat Position                            3256
Key Major                                3256
Key Minor                                3256
Time Signature Numerator                 3256
Time Signature Denominator               3256
Chord Inversion                          3256
Chord Note 1                             3256
Chord Note 2                             3256
Chord Note 3                             3256
Chord Note 4                             3256
Chord Note 5                             3256
Chord Note 6                             3256
Chord Note 7                             3256
Chord Note 8                             3256
dtype: int64

### **Transforming the dataframe into arrays with a specific time resolution**

In [ ]:
pd.set_option('display.max_rows', 1000)
testDataFrame = MainDataFrameBalanced[:10]

testDataFrame
# Testing the result

Transposed Note Pitch Numerical Class  Octave  ...  Chord Note 7  Chord Note 8
0                                      4       4  ...            12            12
1                                      6       4  ...            12            12
2                                      7       4  ...            12            12
3                                     11       4  ...            12            12
4                                      4       4  ...            12            12
5                                      6       4  ...            12            12
6                                      7       4  ...            12            12
7                                      6       5  ...            12            12
8                                      4       5  ...            12            12
9                                      4       5  ...            12            12

[10 rows x 19 columns]

In [ ]:
dfRows, dfCol = MainDataFrameBalanced.shape

TrainRows=int(dfRows*0.8)

TrainDF = MainDataFrameBalanced[:TrainRows]
TestDF = MainDataFrameBalanced[TrainRows:].reset_index(drop=True)

TestDF

Transposed Note Pitch Numerical Class  ...  Chord Note 8
0                                           0  ...            12
1                                           2  ...            12
2                                           0  ...            12
3                                          11  ...            12
4                                           0  ...            12
...                                       ...  ...           ...
185040                                      4  ...            12
185041                                      7  ...            12
185042                                      0  ...            12
185043                                      0  ...            12
185044                                     12  ...            12

[185045 rows x 19 columns]

In [ ]:
def Vectorization(bars,df,resolution, name):
  """"
  This function transforms the chosen dataframe into arrays in order to be used in proper format as inputs and outputs on the model.
  The arrays contain an x number of consecutive bars and a specific time resolution for assumption purposes.
  Resolution:0.25 = 16nths, 0.5=8ths, 1= quarter notes etc
  """
  Main_X=[]
  Main_y=[]

  def vectorize(start,end):
    #print("indexes:",start,end)
    i=start 
    X = []
    y = []  
    currentBar=int(df.iloc[i,4])
    while i<=end:
      divisor = int(df.iloc[i,3]//resolution)
      pitchClass = df.iloc[i,0]
      array= np.full((1, 12), 0, dtype=int)
      if pitchClass != 12:
        array[:,pitchClass] = 1
      arrayWithDiv=np.tile(array,(divisor,1))
      X.append(arrayWithDiv)
      arrayWithDiv = arrayWithDiv.reshape(1, divisor*12, 1)    
      if int(df.iloc[i,4])==currentBar:
        chordArray= np.full((1, 12), 0, dtype=int)
        for col in df[df.columns[11:]]:       
          chClass = int(df[col][i])
          if chClass is not 12:
            chordArray[:,chClass]=1
        y.append(chordArray)
        currentBar+=1
      i+=1    
    X = np.array(X)
    X = np.concatenate( X, axis=0 )
    rows, col = X.shape
    rightNumberofRows = 16/resolution
    if rightNumberofRows>rows:
      dif=int(rightNumberofRows-rows)
      extraRows = np.full((dif, 12), 0, dtype=int)
      X = np.concatenate((X,extraRows))
    elif rightNumberofRows<rows:
      dif=int(abs(rightNumberofRows-rows))
      X = X[:-dif, :]
    n_timesteps= int(rightNumberofRows*12)
    y = np.array(y)
    y = np.concatenate( y, axis=0 )
    return X,y        
  
  def lastModulo(i):
    while i< len(df)-1:
      if df.iloc[i+1,4]==df.iloc[i,4]:
        lastMod= i+1
      else:
        lastMod= i
        break
      i+=1   
    return lastMod

  def isItAscending(i):
    if df.iloc[i,4]>=df.iloc[i-1,4]:
      flag=True
    else:
      flag=False
    return flag

  # Begin row iteration
  row=0
  current=0
  currentEnd=0
  while row < len(df):
    if row!=0:     
      if not isItAscending(row):
        #print(row,isItAscending(row))
        current=row
    if df.iloc[row,4]%bars!=0:
      pass
    else:
      currentStart = current
      currentEnd = lastModulo(row)
      X,y=vectorize(currentStart,currentEnd)
      Main_X.append(X)
      Main_y.append(y)
      current = currentEnd+1
      row=currentEnd
    if row%1000==0:
      print(row,'row')
    row+=1
  print("Done")
  np.savez(name+'.npz', X=Main_X, y=Main_y)



In [5]:
def reshaping(j, array):
  X =array['X'][j]
  y=array['y'][j]
  shapeDiff=X.shape[0]-y.shape[0]
  y_padding= np.full((shapeDiff, 12), 0, dtype=int)
  y = np.concatenate((y, y_padding), axis=0)
  X=X.reshape(1, n, 1).astype(np.float32)
  y=y.reshape(1, n, 1).astype(np.float32)
  return X,y

def reshapeEval(y1,y2):
  y1=y1.reshape(64,12)
  y2=y2.reshape(64,12)
  y1=np.delete(y1, slice(4, 64), 0)
  y2=np.delete(y2, slice(4, 64), 0)
  y1=y1.reshape(1, 48, 1)
  y2=y2.reshape(1, 48, 1)
  return y1,y2

In [ ]:
Vectorization(4, TrainDF, 0.25, "TrainDF")

0 row
1000 row
2000 row
3000 row
6000 row
8000 row
9000 row
10000 row
11000 row
12000 row
13000 row
15000 row
16000 row
17000 row
19000 row
20000 row
22000 row
23000 row
24000 row
25000 row
26000 row
27000 row
29000 row
30000 row
31000 row
32000 row
33000 row
34000 row
35000 row
36000 row
37000 row
39000 row
40000 row
41000 row
42000 row
43000 row
44000 row
45000 row
46000 row
47000 row
48000 row
50000 row
51000 row
52000 row
53000 row
54000 row
55000 row
56000 row
57000 row
58000 row
59000 row
61000 row
63000 row
64000 row
65000 row
66000 row
67000 row
68000 row
70000 row
71000 row
72000 row
74000 row
75000 row
76000 row
77000 row
79000 row
80000 row
81000 row
83000 row
84000 row
85000 row
87000 row
89000 row
90000 row
91000 row
92000 row
93000 row
94000 row
95000 row
96000 row
97000 row
99000 row
100000 row
101000 row
103000 row
104000 row
105000 row
106000 row
107000 row
108000 row
109000 row
111000 row
112000 row
113000 row
114000 row
115000 row
116000 row
117000 row
118000 row
119

In [ ]:
Vectorization(4, TestDF, 0.25, "TestDF")

0 row
1000 row
2000 row
3000 row
4000 row
6000 row
8000 row
10000 row
11000 row
12000 row
13000 row
14000 row
15000 row
16000 row
17000 row
18000 row
19000 row
20000 row
21000 row
22000 row
23000 row
24000 row
25000 row
26000 row
27000 row
28000 row
29000 row
30000 row
31000 row
32000 row
33000 row
34000 row
35000 row
36000 row
37000 row
39000 row
40000 row
41000 row
42000 row
43000 row
44000 row
45000 row
46000 row
47000 row
48000 row
49000 row
50000 row
51000 row
52000 row
53000 row
54000 row
56000 row
57000 row
58000 row
59000 row
60000 row
61000 row
62000 row
63000 row
64000 row
66000 row
67000 row
68000 row
71000 row
72000 row
73000 row
74000 row
75000 row
76000 row
77000 row
78000 row
79000 row
80000 row
82000 row
83000 row
84000 row
85000 row
86000 row
88000 row
90000 row
91000 row
92000 row
93000 row
94000 row
95000 row
96000 row
97000 row
98000 row
99000 row
101000 row
102000 row
103000 row
104000 row
105000 row
106000 row
107000 row
108000 row
109000 row
110000 row
111000 row

### **BLSTM Implementation**

Experiment 1

In [ ]:
n=768
# Load arrays
arrays = np.load('/content/drive/My Drive/Colab Notebooks/TrainDF.npz',allow_pickle=True)

# Define BLSTM
model = Sequential()
model.add(Bidirectional(LSTM(20, return_sequences=True), input_shape=(n, 1)))
model.add(TimeDistributed(Dense(1, activation='sigmoid')))
model.add(Dropout(0.2))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

for i in range(len(arrays['X'])):
  X,y=reshaping(i,arrays)
  print(i)
  # Fit model
  model.fit(X, y, epochs=1, batch_size=1, verbose=2)


Streaming output truncated to the last 5000 lines.
1/1 - 0s - loss: 0.0395 - accuracy: 0.9909
44174
1/1 - 0s - loss: 0.0853 - accuracy: 0.9857
44175
1/1 - 0s - loss: 0.0861 - accuracy: 0.9831
44176
1/1 - 0s - loss: 0.0518 - accuracy: 0.9818
44177
1/1 - 0s - loss: 0.0470 - accuracy: 0.9857
44178
1/1 - 0s - loss: 0.0626 - accuracy: 0.9870
44179
1/1 - 0s - loss: 0.0655 - accuracy: 0.9831
44180
1/1 - 0s - loss: 0.1029 - accuracy: 0.9844
44181
1/1 - 0s - loss: 0.0842 - accuracy: 0.9870
44182
1/1 - 0s - loss: 0.0413 - accuracy: 0.9805
44183
1/1 - 0s - loss: 0.1017 - accuracy: 0.9844
44184
1/1 - 0s - loss: 0.0938 - accuracy: 0.9766
44185
1/1 - 0s - loss: 0.1056 - accuracy: 0.9844
44186
1/1 - 0s - loss: 0.0599 - accuracy: 0.9779
44187
1/1 - 0s - loss: 0.0881 - accuracy: 0.9818
44188
1/1 - 0s - loss: 0.1095 - accuracy: 0.9818
44189
1/1 - 0s - loss: 0.0288 - accuracy: 0.9857
44190
1/1 - 0s - loss: 0.0737 - accuracy: 0.9805
44191
1/1 - 0s - loss: 0.0447 - accuracy: 0.9857
44192
1/1 - 0s - loss: 0

### **Evaluate BLSTM**

In [ ]:
test_arrays = np.load('/content/drive/My Drive/Colab Notebooks/TestDF.npz',allow_pickle=True)

total_accuracy=[]
# evaluate LSTM
for i in range(len(test_arrays['X'])):
  X,y=reshaping(i,arrays)
  shapeDiff=X.shape[0]-y.shape[0]
  ypred = model.predict_classes(y, verbose=0)
  y,ypred = reshapeEval(y,ypred)
  tolerance = 1e-10
  accuracy = (np.abs(ypred - y) < tolerance ).all(axis=(0,2)).mean()
  total_accuracy.append(accuracy)
  if i%1000==0:
    print(i,'row')
    print("Accuracy:",accuracy)
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")


Instructions for updating:
Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
0 row
Accuracy: 0.7083333333333334
1000 row
Accuracy: 0.7083333333333334
2000 row
Accuracy: 0.7708333333333334
3000 row
Accuracy: 0.75
4000 row
Accuracy: 0.75
5000 row
Accuracy: 0.8541666666666666
6000 row
Accuracy: 0.7916666666666666
7000 row
Accuracy: 1.0
8000 row
Accuracy: 0.75
9000 row
Accuracy: 0.6666666666666666
10000 row
Accuracy: 0.8333333333333334
11000 row
Accuracy: 0.8333333333333334
12000 row
Accuracy: 0.7291666666666666
-------------------------------------
Mean Accuracy: 0.7793780068728521
-------------------------------------


In [ ]:
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")
print("Standard Deviation:", np.std(total_accuracy))
print("-------------------------------------")

-------------------------------------
Mean Accuracy: 0.7793780068728521
-------------------------------------
Standard Deviation: 0.06585289202464169
-------------------------------------


Experiment 2

In [ ]:
n=768
# Load arrays
arrays = np.load('/content/drive/My Drive/Colab Notebooks/TrainDF.npz',allow_pickle=True)

# Define BLSTM
model = Sequential()
model.add(Bidirectional(LSTM(64, return_sequences=True), input_shape=(n, 1)))
model.add(Bidirectional(LSTM(64, return_sequences=True), input_shape=(n, 1)))
model.add(TimeDistributed(Dense(1, activation='sigmoid')))
model.add(Dropout(0.2))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

for i in range(len(arrays['X'])):
  X,y=reshaping(i,arrays)
  print(i)
  # Fit model
  model.fit(X, y, epochs=1, batch_size=1, verbose=2)

Streaming output truncated to the last 5000 lines.
1/1 - 0s - loss: 0.0338 - accuracy: 0.9961
44174
1/1 - 0s - loss: 0.0407 - accuracy: 0.9857
44175
1/1 - 0s - loss: 0.0796 - accuracy: 0.9909
44176
1/1 - 0s - loss: 0.0441 - accuracy: 0.9831
44177
1/1 - 0s - loss: 0.1209 - accuracy: 0.9844
44178
1/1 - 0s - loss: 0.0756 - accuracy: 0.9896
44179
1/1 - 0s - loss: 0.0380 - accuracy: 0.9935
44180
1/1 - 0s - loss: 0.0589 - accuracy: 0.9870
44181
1/1 - 0s - loss: 0.0954 - accuracy: 0.9857
44182
1/1 - 0s - loss: 0.0826 - accuracy: 0.9844
44183
1/1 - 0s - loss: 0.0850 - accuracy: 0.9844
44184
1/1 - 0s - loss: 0.0935 - accuracy: 0.9753
44185
1/1 - 0s - loss: 0.1358 - accuracy: 0.9831
44186
1/1 - 0s - loss: 0.1032 - accuracy: 0.9857
44187
1/1 - 0s - loss: 0.0918 - accuracy: 0.9792
44188
1/1 - 0s - loss: 0.0441 - accuracy: 0.9844
44189
1/1 - 0s - loss: 0.0594 - accuracy: 0.9883
44190
1/1 - 0s - loss: 0.1220 - accuracy: 0.9779
44191
1/1 - 0s - loss: 0.0777 - accuracy: 0.9870
44192
1/1 - 0s - loss: 0

In [ ]:
test_arrays = np.load('/content/drive/My Drive/Colab Notebooks/TestDF.npz',allow_pickle=True)

total_accuracy=[]
# evaluate LSTM
for i in range(len(test_arrays['X'])):
  X,y=reshaping(i,arrays)
  shapeDiff=X.shape[0]-y.shape[0]
  ypred = model.predict_classes(y, verbose=0)
  y,ypred = reshapeEval(y,ypred)
  tolerance = 1e-10
  accuracy = (np.abs(ypred - y) < tolerance ).all(axis=(0,2)).mean()
  total_accuracy.append(accuracy)
  if i%1000==0:
    print(i,'row')
    print("Accuracy:",accuracy)
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")

Instructions for updating:
Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
0 row
Accuracy: 0.7291666666666666
1000 row
Accuracy: 0.7916666666666666
2000 row
Accuracy: 0.8333333333333334
3000 row
Accuracy: 0.8541666666666666
4000 row
Accuracy: 0.7291666666666666
5000 row
Accuracy: 0.8958333333333334
6000 row
Accuracy: 0.8125
7000 row
Accuracy: 0.9166666666666666
8000 row
Accuracy: 0.7291666666666666
9000 row
Accuracy: 0.7083333333333334
10000 row
Accuracy: 0.8541666666666666
11000 row
Accuracy: 0.8333333333333334
12000 row
Accuracy: 0.7916666666666666
-------------------------------------
Mean Accuracy: 0.7980532646048111
-------------------------------------


In [26]:
print("Standard Deviation:", np.std(total_accuracy))

Standard Deviation: 0.05624358548274352


Experiment 3

In [6]:
n=768
# Load arrays
arrays = np.load('/content/drive/My Drive/Colab Notebooks/TrainDF.npz',allow_pickle=True)

# Define BLSTM
model = Sequential()
model.add(Bidirectional(LSTM(128, return_sequences=True), input_shape=(n, 1)))
model.add(Bidirectional(LSTM(128, return_sequences=True), input_shape=(n, 1)))
model.add(TimeDistributed(Dense(1, activation='sigmoid')))
model.add(Dropout(0.2))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

for i in range(len(arrays['X'])):
  X,y=reshaping(i,arrays)
  print(i)
  # Fit model
  model.fit(X, y, epochs=1, batch_size=1, verbose=2)

Streaming output truncated to the last 5000 lines.
1/1 - 0s - loss: 0.0148 - accuracy: 0.9961
44174
1/1 - 0s - loss: 0.0391 - accuracy: 0.9870
44175
1/1 - 0s - loss: 0.0207 - accuracy: 0.9922
44176
1/1 - 0s - loss: 0.0253 - accuracy: 0.9831
44177
1/1 - 0s - loss: 0.0243 - accuracy: 0.9883
44178
1/1 - 0s - loss: 0.0355 - accuracy: 0.9909
44179
1/1 - 0s - loss: 0.0405 - accuracy: 0.9909
44180
1/1 - 0s - loss: 0.0783 - accuracy: 0.9857
44181
1/1 - 0s - loss: 0.0599 - accuracy: 0.9870
44182
1/1 - 0s - loss: 0.1240 - accuracy: 0.9792
44183
1/1 - 0s - loss: 0.1179 - accuracy: 0.9857
44184
1/1 - 0s - loss: 0.1155 - accuracy: 0.9753
44185
1/1 - 0s - loss: 0.1526 - accuracy: 0.9857
44186
1/1 - 0s - loss: 0.0813 - accuracy: 0.9857
44187
1/1 - 0s - loss: 0.0536 - accuracy: 0.9792
44188
1/1 - 0s - loss: 0.0443 - accuracy: 0.9857
44189
1/1 - 0s - loss: 0.0802 - accuracy: 0.9870
44190
1/1 - 0s - loss: 0.1194 - accuracy: 0.9831
44191
1/1 - 0s - loss: 0.0772 - accuracy: 0.9896
44192
1/1 - 0s - loss: 0

In [7]:
test_arrays = np.load('/content/drive/My Drive/Colab Notebooks/TestDF.npz',allow_pickle=True)

total_accuracy=[]
# evaluate LSTM
for i in range(len(test_arrays['X'])):
  X,y=reshaping(i,arrays)
  shapeDiff=X.shape[0]-y.shape[0]
  ypred = model.predict_classes(y, verbose=0)
  y,ypred = reshapeEval(y,ypred)
  tolerance = 1e-10
  accuracy = (np.abs(ypred - y) < tolerance ).all(axis=(0,2)).mean()
  total_accuracy.append(accuracy)
  if i%1000==0:
    print(i,'row')
    print("Accuracy:",accuracy)
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")

Instructions for updating:
Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
0 row
Accuracy: 0.75
1000 row
Accuracy: 0.8333333333333334
2000 row
Accuracy: 0.8958333333333334
3000 row
Accuracy: 0.875
4000 row
Accuracy: 0.7708333333333334
5000 row
Accuracy: 0.9375
6000 row
Accuracy: 0.7708333333333334
7000 row
Accuracy: 0.9375
8000 row
Accuracy: 0.7708333333333334
9000 row
Accuracy: 0.75
10000 row
Accuracy: 0.8541666666666666
11000 row
Accuracy: 0.8125
12000 row
Accuracy: 0.8125
-------------------------------------
Mean Accuracy: 0.8178883161512028
-------------------------------------


In [9]:
print("Standard Deviation:", np.std(total_accuracy))

Standard Deviation: 0.0652932267039047


### **Evaluation - Comparison with other models**

**Simple LSTM**

In [ ]:
n=768
# Load arrays
arrays = np.load('/content/drive/My Drive/Colab Notebooks/TrainDF.npz',allow_pickle=True)

# Define LSTM
model = Sequential()
model.add(LSTM(20, return_sequences=True))
model.add(TimeDistributed(Dense(1, activation='sigmoid')))
model.add(Dropout(0.2))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

for i in range(len(arrays['X'])):
  X,y=reshaping(i,arrays)
  print(i)
  # Fit model
  model.fit(X, y, epochs=1, batch_size=1, verbose=2, callbacks=[cp_callback])

Streaming output truncated to the last 5000 lines.

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.0572 - accuracy: 0.9792
45424

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.1815 - accuracy: 0.9818
45425

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.0751 - accuracy: 0.9779
45426

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.1081 - accuracy: 0.9818
45427

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.0872 - accuracy: 0.9857
45428

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.0915 - accuracy: 0.9818
45429

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.1112 - accuracy: 0.9779
45430

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.1158 - accuracy: 0.9740
45431

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0.1262 - accuracy: 0.9805
45432

Epoch 00001: saving model to training_1/cp.ckpt
1/1 - 0s - loss: 0

Testing

In [ ]:
test_arrays = np.load('/content/drive/My Drive/Colab Notebooks/TestDF.npz',allow_pickle=True)

total_accuracy=[]
# evaluate LSTM
for i in range(len(test_arrays['X'])):
  X,y=reshaping(i,arrays)
  shapeDiff=X.shape[0]-y.shape[0]
  ypred = model.predict_classes(y, verbose=0)
  y,ypred = reshapeEval(y,ypred)
  tolerance = 1e-10
  accuracy = (np.abs(ypred - y) < tolerance ).all(axis=(0,2)).mean()
  total_accuracy.append(accuracy)
  if i%1000==0:
    print(i,'row')
    print("Accuracy:",accuracy)
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")
print("Standard Deviation:", np.std(total_accuracy))
print("-------------------------------------")

Instructions for updating:
Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
0 row
Accuracy: 0.8333333333333334
1000 row
Accuracy: 0.8125
2000 row
Accuracy: 0.8333333333333334
3000 row
Accuracy: 0.8541666666666666
4000 row
Accuracy: 0.8333333333333334
5000 row
Accuracy: 0.875
6000 row
Accuracy: 0.875
7000 row
Accuracy: 1.0
8000 row
Accuracy: 0.8333333333333334
9000 row
Accuracy: 0.8333333333333334
10000 row
Accuracy: 0.875
11000 row
Accuracy: 0.8541666666666666
12000 row
Accuracy: 0.8125
-------------------------------------
Mean Accuracy: 0.860458762886598
-------------------------------------
Standard Deviation: 0.03641274174141592
-------------------------------------


**Simle RNN**

In [ ]:
n=768
# Load arrays
arrays = np.load('/content/drive/My Drive/Colab Notebooks/TrainDF.npz',allow_pickle=True)

# Define RNN
model = Sequential()
model.add(SimpleRNN(20, return_sequences=True))
model.add(TimeDistributed(Dense(1, activation='sigmoid')))
model.add(Dropout(0.2))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])


for i in range(len(arrays['X'])):
  X,y=reshaping(i,arrays)
  print(i)

  # Fit model
  model.fit(X, y, epochs=1, batch_size=1, verbose=2)

0

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.7506 - accuracy: 0.3255
1

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.7944 - accuracy: 0.2852
2

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.8587 - accuracy: 0.2904
3

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.7226 - accuracy: 0.3398
4

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.7027 - accuracy: 0.3385
5

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.6345 - accuracy: 0.5260
6

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.6076 - accuracy: 0.6445
7

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.5388 - accuracy: 0.7604
8

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.6112 - accuracy: 0.8086
9

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.5088 - accuracy: 0.9245
10

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s

Exception ignored in: <bound method NpzFile.__del__ of <numpy.lib.npyio.NpzFile object at 0x7f9e098283c8>>
Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/numpy/lib/npyio.py", line 230, in __del__
    self.close()
  File "/usr/local/lib/python3.6/dist-packages/numpy/lib/npyio.py", line 225, in close
    self.fid.close()
OSError: [Errno 107] Transport endpoint is not connected


Streaming output truncated to the last 5000 lines.

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.1100 - accuracy: 0.9779
45424

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0900 - accuracy: 0.9805
45425

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.1497 - accuracy: 0.9779
45426

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0950 - accuracy: 0.9779
45427

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0858 - accuracy: 0.9831
45428

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0728 - accuracy: 0.9779
45429

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0923 - accuracy: 0.9779
45430

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0616 - accuracy: 0.9727
45431

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0.0728 - accuracy: 0.9805
45432

Epoch 00001: saving model to training_2/cp.ckpt
1/1 - 0s - loss: 0

Testing

In [ ]:
test_arrays = np.load('/content/drive/My Drive/Colab Notebooks/TestDF.npz',allow_pickle=True)

total_accuracy=[]
# evaluate Simple RNN
for i in range(len(test_arrays['X'])):
  X,y=reshaping(i,arrays)
  shapeDiff=X.shape[0]-y.shape[0]
  ypred = model.predict_classes(y, verbose=0)
  y,ypred = reshapeEval(y,ypred)
  tolerance = 1e-10
  accuracy = (np.abs(ypred - y) < tolerance ).all(axis=(0,2)).mean()
  total_accuracy.append(accuracy)
  if i%1000==0:
    print(i,'row')
    print("Accuracy:",accuracy)
print("-------------------------------------")
print("Mean Accuracy:", np.mean(total_accuracy))
print("-------------------------------------")
print("Standard Deviation:", np.std(total_accuracy))
print("-------------------------------------")

0 row
Accuracy: 0.8541666666666666
1000 row
Accuracy: 0.7708333333333334
2000 row
Accuracy: 0.7916666666666666
3000 row
Accuracy: 0.7916666666666666
4000 row
Accuracy: 0.7708333333333334
5000 row
Accuracy: 0.8333333333333334
6000 row
Accuracy: 0.7708333333333334
7000 row
Accuracy: 0.9583333333333334
8000 row
Accuracy: 0.7916666666666666
9000 row
Accuracy: 0.7083333333333334
10000 row
Accuracy: 0.7708333333333334
11000 row
Accuracy: 0.7916666666666666
12000 row
Accuracy: 0.7916666666666666
-------------------------------------
Mean Accuracy: 0.8114828178694159
-------------------------------------
Standard Deviation: 0.056696820785067555
-------------------------------------
